# Scratch Code

copy/paste code for debugging

In [1]:
from tqdm import tqdm_notebook

# PERCEPT STUFF

In [6]:
####
######## GROUP templates are in ROI verts and not in valid verts of percept.. is this something i need to change? 
######## realized this when the subj temlates had like 274 vox and group had 324 for SL 22 right hem (20210913)
######## ok so its ironic that for the subj templates i have fewer vertices
######## this is because i do the valid verts check for all subj and then use that on the perception stuff of each subj
######## when i should do the opposite, have the group have this thing.. need to fix this..?
######## make sure that it wasnt on purpose.. but in anycase, i do use valid verts for group, i just made total array big via roi_verts rather than valid_verts


import sys
# sys.path.append('../')
# #import time

import numpy as np
import deepdish as dd
import os
from scipy.stats import zscore

import nibabel as nib #use to load mmp atlas

import h5py

from _deconvolve import *

from _functions import * #import the story schema effect scoring function

################
################ INPUTS
################


# date = 20211014
# hem = 'R'
# roi = 'SL'
# roi_id = 22
# scoretype = 'sl_percept_score'
# modality_mode = 'within_modality'


date = 20211014
hem = 'L'
roi = 'Ang'
roi_id = 9999
scoretype = 'sl_percept_score'
modality_mode = 'within_modality'

# date = sys.argv[1] # 'date label to use'
# hem = str(sys.argv[2]) # 'L' or 'R'
# roi = sys.argv[3] # 'STS', 'SL', 'atlas'
# roi_id = int(sys.argv[4]) # "9999" or int
# scoretype = sys.argv[5] # "sl_percept_scores" or any directory name that makes sense
# modality_mode = str(sys.argv[6]) #within_modality or across_modality


################
################ FUNCTIONS 
################

def RunPerceptionSimilarityMatrix(roi_verts,percept,hem):
    '''
    roi_verts is False bool array of shape 40962 with TRUE indicating ROI vertices
    timeseries is dict of hem and story for all subjects
    '''
    

    valid_verts = roi_verts.copy()
    for story in stories:
        valid_verts = valid_verts * ~np.any(np.any(np.isnan(percept[story]), axis=2), axis=1) #(np.any(np.all(~np.isnan(percept[story]), axis=2), axis=1))#(~np.any(np.all(np.isnan(percept[story]), axis=2), axis=1))#(np.any(np.all(~np.isnan(percept[story]), axis=2), axis=1))

    print(roi_verts.sum(), valid_verts.sum())

    dim = valid_verts.sum()
    
    subj_templates = np.zeros((nSubj,nStories, dim, 4)) # hold betas for each subject // 20201127

    dim = roi_verts.sum()    

    ### set up event template array and run GLM for full N group (will serve as template later)
    group = np.full((nStories, roi_verts.sum(), 4), fill_value=np.nan) #group average of betas (includes left out subject)
    for st,story in enumerate(stories):
        group_valid = np.logical_and(roi_verts,np.all(~np.isnan(percept[story][:,0,:]),axis=1)) 
        group_idx = np.arange(valid_verts.sum()) #useful for indexing
#         group_mean = np.nanmean(percept[story][roi_verts], axis=2)
        group_mean = np.nanmean(percept[story][valid_verts], axis=2)
        group[st, group_idx, :] = zscore(deconv(group_mean, design_intact[st])[:, 1:], axis=0, ddof=1)

    ### set up similarity matrix array
    loo_story_corr = np.zeros((nStories,nStories,nSubj)) #dont really use this. # REMOVE later?
    loo_ev_corr = np.zeros((nStories, nStories,4,nSubj))

    ### Create similarity matrix for each left-out subject
    for s in tqdm_notebook(range(nSubj)):

        ### LOO group stuff
        loo_subj_betas = np.full((nStories, dim, 4),fill_value=np.nan)
        loo_group_betas = np.full((nStories, dim, 4), fill_value=np.nan)

        ### estimate betas for left-out-subject's stories
        for st,story in enumerate(stories):
            
            ### gather valid_verts across the participants for this story
            valid_verts = np.logical_and(roi_verts,(~np.isnan(percept[story][:,0,s]))) 
            valid_idx = np.arange(valid_verts.sum())

            ### get left-out-subject's story timeseries at perception
            loo_subj = percept[story][valid_verts][:,:,s]  

            ### get average timeseries for this story across N-1 group
            loo_group_mean = np.nanmean(percept[story][valid_verts][:,:,np.arange(nSubj)!=s], axis=2)

            ### Run GLM for loo_subj and loo_group; maximize valid verts for later within-subj templates
            loo_subj_betas[st,valid_idx,:] = zscore(deconv(loo_subj, design_intact[st])[:, 1:], axis=0, ddof=1)
            loo_group_betas[st,valid_idx,:] =  zscore(deconv(loo_group_mean[:,:], design_intact[st])[:, 1:], axis=0, ddof=1)
            
            ## nov 2021
            current_valid = ~(np.all(np.isnan(loo_subj_betas[st,:,:]),1))
            print(current_valid.sum(), current_valid.shape)
            subj_templates[s,st,:,:] = loo_subj_betas[st,current_valid,:]

        ### calculate similarity matrix
        #### run correlation of left-out-subject's stories with N-1 group's stories
        for ev in range(4):
                                         
            ### Check for lowest common denominator of valid vertices across stories
            valids_all = np.all(~np.isnan(loo_subj_betas[:,:,ev]),axis=0)                                         
                                       
            print('valids_all: ',valids_all.sum())

            ### Correlate every event of loo_subj with N-1 group
            loo_ev_corr[:,:,ev,s] = np.dot(loo_subj_betas[:,valids_all,ev], loo_group_betas[:,valids_all,ev].T)/(dim-1)#(dim-1)

            ### symmetrize
            loo_ev_corr[:,:,ev,s] = (loo_ev_corr[:,:,ev,s] + loo_ev_corr[:,:,ev,s].T)/2 #make N-1 mat symmetric per event

    return group, subj_templates, loo_ev_corr



# def RunPerceptionSimilarityMatrix(roi_verts,timeseries,hem):
#     '''
#     roi_verts is False bool array of shape 40962 with TRUE indicating ROI vertices
#     timeseries is dict of hem and story for all subjects
#     '''

#     dim = roi_verts.sum() # identify number of vertices in specified ROI

#     ### set up event template array
#     group = np.zeros((nStories, dim, 4)) #group average including left out subject 
#     for st, story in enumerate(stories):
#         ### Run GLM for full N group (will serve as template later)
#         group_mean = (np.nanmean(percept[story][roi_verts][:,:,:], axis=2))
#         group[st, :, :] = zscore(deconv(group_mean, design_intact[st])[:, 1:], axis=0, ddof=1)


#     ### set up similarity matrix array
#     loo_story_corr = np.zeros((nStories,nStories,nSubj)) #dont really use this. # REMOVE later?
#     loo_ev_corr = np.zeros((nStories, nStories,4,nSubj))

#     #     group_ev_corr = np.zeros((nStories, nStories,4,nSubj))

#     for s in tqdm_notebook(range(nSubj)):

#         ### LOO group stuff
#         loo_subj_betas = np.full((nStories, dim, 4),fill_value=np.nan)
#         loo_group_betas = np.full((nStories, dim, 4), fill_value=np.nan)

#         ### ALL SUBJECTS GROUP STUFF
#         group_betas = np.zeros((nStories, dim, 4))

#         ### estimate betas for left-out-subject's stories
#         for st,story in enumerate(stories):
#             # find valid verts for this subject that intersect with our region of interest
#             valid_verts = np.logical_and(roi_verts,(~np.isnan(percept[story][:,0,s]))) 
#             valid_idx = np.arange(valid_verts.sum()) #useful for indexing

#             ### get left-out-subject's story timeseries at perception
#             loo_subj = percept[story][valid_verts][:,:,s]  

#             ### get average timeseries for this story across N-1 group
#             loo_group_mean = np.nanmean(percept[story][valid_verts][:,:,np.arange(nSubj)!=s], axis=2)

#             ### Run GLM for loo_subj and loo_group 
#             loo_subj_betas[st,valid_idx,:] = zscore(deconv(loo_subj, design_intact[st])[:, 1:], axis=0, ddof=1)
#             loo_group_betas[st,valid_idx,:] =  zscore(deconv(loo_group_mean[:,:], design_intact[st])[:, 1:], axis=0, ddof=1)


#         ### calculate similarity matrix
#         #### run correlation of left-out-subject's stories with N-1 group's stories
#         print()
#         for ev in range(4):

#             ### Check for lowest common denominator of valid vertices across stories
#             allstoryvalids = np.all(~np.isnan(loo_subj_betas[:,:,ev]),axis=0)
#             print(allstoryvalids.sum())

#     #         allstoryvalids = [(~np.isnan(loo_subj_betas[st,:,ev])) for st in range(16)]
#     #         allstoryvalids = np.where(np.all(np.stack(allstoryvalids,axis=0),axis=0))[0]
#     # #         allstoryvalids = np.arange(np.all(~np.isnan(loo_subj_betas[:,:,ev]),axis=0).sum())
#     #         print(np.any(~np.isnan(loo_subj_betas[:,:,ev]),axis=0).sum(),np.all(~np.isnan(loo_subj_betas[:,:,ev]),axis=0).sum())
#     #         print(s, len(np.unique(allstoryvalids)), allstoryvalids.shape)
#     #         print((valid_idx==allstoryvalids).sum())

#             ### Correlate every event of loo_subj with N-1 group
#             loo_ev_corr[:,:,ev,s] = np.dot(loo_subj_betas[:,allstoryvalids,ev], loo_group_betas[:,allstoryvalids,ev].T)/(len(allstoryvalids)-1)#(dim-1)

#             ### symmetrize
#             loo_ev_corr[:,:,ev,s] = (loo_ev_corr[:,:,ev,s] + loo_ev_corr[:,:,ev,s].T)/2 #make N-1 ISC symmetric per event

#     return group, loo_ev_corr






In [7]:
################
################ CONSTANTS & DESIGN MATRIX
################

stories = ['Brazil',  'Derek', 'MrBean',   'PulpFiction',
           'BigBang', 'Santa', 'Shame',    'Vinny',
           'DueDate', 'GLC',   'KandD',    'Nonstop',
           'Friends', 'HIMYM', 'Seinfeld', 'UpInTheAir']

nSubj = 31
TR = 1.5
nStories = len(stories)

# Story event boundaries (in seconds)
events_seconds_intact = np.array([
     [0,     6,    46,    73,   115,   184],
     [0,     6,    30,   111,   169,   188],
     [0,     6,    21,    74,   159,   186],
     [0,     6,    40,    56,   171,   185],
     [0,     6,    31,    46,   156,   171],
     [0,     6,    71,   104,   165,   175],
     [0,     6,    26,    94,   134,   175],
     [0,     6,    28,    59,   151,   179],
     [0,     6,    51,   111,   122,   189],
     [0,     6,    23,    70,    84,   171],
     [0,     6,    53,    82,   136,   184],
     [0,     6,    29,    77,   123,   190],
     [0,     6,    30,    97,   138,   163],
     [0,     6,    36,   109,   124,   169],
     [0,     6,    39,    85,   107,   173],
     [0,     6,    33,   108,   144,   187]])

# Story lengths (in TRs)
story_TRs = np.array([124, 126, 125, 124,
                      115, 118, 118, 120,
                      127, 115, 124, 128,
                      110, 114, 116, 126])


# Compute design matrices for all stories
design_intact = []
for i in range(len(stories)):
    subevent_E = np.zeros((events_seconds_intact[i, 5], 5))
    for e in range(5):
        subevent_E[events_seconds_intact[i, e]:
                   (events_seconds_intact[i, e + 1] + 1), e] = 1
    design_intact.append(regressor_to_TR(subevent_E[:,:], TR, story_TRs[i]))
design_intact = np.array(design_intact)


################
################ RUN ANALYSIS
################

# ### IMPORT perception timeseries
# percept_path = '/jukebox/norman/rmasis/clones/SchemaBigFiles/FullPerceptRecall'
# percept = dd.io.load(os.path.join(percept_path,'wholebrain_perception.h5'),'/'+hem) #perception timeseries, shape for a story: (nTRs,40962)

percept_path = '../../SchemaBigFiles/FullPerceptRecall'

### IMPORT perception timeseries
if 'hippo' in roi:
#     percept = dd.io.load(os.path.join(percept_path,"hipp_perception_recall.h5"))['perception']
    percept = dd.io.load(os.path.join(percept_path,"hipp_perception.h5"))
else:
    percept = dd.io.load(os.path.join(percept_path,'wholebrain_perception.h5'),'/'+hem) #perception timeseries, shape for a story: (nTRs,40962)


### GET VERTS FOR THIS ROI (whether searchlight, atlas or specific roi)
roi_verts = ExtractROI(roi,roi_id,hem)

In [4]:
roi_verts.sum()

1120

In [8]:
subj_templates[20]

array([[[ 1.50829641, -1.0831311 , -0.53226394,  0.3478544 ],
        [-1.65104618, -0.48023361, -0.59694252,  0.3450657 ],
        [ 0.99307734,  1.60105913,  1.37815308, -1.15789085],
        ...,
        [ 0.31418918,  0.1388377 ,  1.02894707, -1.2641663 ],
        [-1.24065462, -1.8438217 , -0.56440908,  1.50211008],
        [ 1.08306162, -2.4127612 , -0.55562894,  1.79577683]],

       [[-0.94395498,  1.15173465, -1.57424745, -1.38429874],
        [-0.99792479,  0.32977621, -1.22691468, -0.64488817],
        [ 0.79643644, -0.38630719, -0.0794215 ,  0.32224034],
        ...,
        [-0.61370986,  1.63781069, -2.0480198 , -1.58676908],
        [-2.70363625,  0.40682023,  0.73345506,  1.08450698],
        [-1.27906032,  1.03660943,  0.4273224 ,  0.67709103]],

       [[-0.51166569,  0.50106886, -0.40397185, -0.87216387],
        [-0.41593252,  0.44596542, -1.00336828, -0.71870458],
        [ 1.59230912, -1.89684306,  1.06073094,  1.01981317],
        ...,
        [        nan,      

In [58]:
subj_templates[20]

array([[[ 1.50829641, -1.0831311 , -0.53226394,  0.3478544 ],
        [-1.65104618, -0.48023361, -0.59694252,  0.3450657 ],
        [ 0.99307734,  1.60105913,  1.37815308, -1.15789085],
        ...,
        [ 0.31418918,  0.1388377 ,  1.02894707, -1.2641663 ],
        [-1.24065462, -1.8438217 , -0.56440908,  1.50211008],
        [ 1.08306162, -2.4127612 , -0.55562894,  1.79577683]],

       [[-0.94395498,  1.15173465, -1.57424745, -1.38429874],
        [-0.99792479,  0.32977621, -1.22691468, -0.64488817],
        [ 0.79643644, -0.38630719, -0.0794215 ,  0.32224034],
        ...,
        [-0.61370986,  1.63781069, -2.0480198 , -1.58676908],
        [-2.70363625,  0.40682023,  0.73345506,  1.08450698],
        [-1.27906032,  1.03660943,  0.4273224 ,  0.67709103]],

       [[-0.51166569,  0.50106886, -0.40397185, -0.87216387],
        [-0.41593252,  0.44596542, -1.00336828, -0.71870458],
        [ 1.59230912, -1.89684306,  1.06073094,  1.01981317],
        ...,
        [        nan,      

In [8]:
### RUN SIMILARITY MATRIX
group, subj_templates, loo_ev_corr = RunPerceptionSimilarityMatrix(roi_verts,percept,hem)

nPerm = 1

### RUN STORY AND SCHEMA SCORING
nEvents= 4
story_effect = np.zeros((nSubj,nStories,nEvents,nPerm+1)) 
schema_effect = np.zeros((nSubj,nStories,nEvents,nPerm+1)) 

### get story and schema scores for each event
for ev in range(nEvents):
#     story_effect[:,:,ev,:], schema_effect[:,:,ev,:] = GetStorySchemaEffect(loo_ev_corr[:,:,ev,:],test_mod='across_modality')
    story_effect[:,:,ev,:], schema_effect[:,:,ev,:] = GetStorySchemaEffect(loo_ev_corr[:,:,ev,:],test_mod=modality_mode,nPerm=nPerm)
    
################
################ FILE SAVING 
################

path = '../../SchemaBigFiles/_PaperOutputData'

# if roi in ['mPFC', 'PMC', 'Aud', 'MTN', 'PM', 'MP','AT','STS','SFG']:
#     savedir = 'roi_{}'.format(scoretype)
# elif roi == 'atlas':
#     savedir = 'roi_{}'.format(scoretype)
# elif roi.lower() == 'sl':
#     savedir = 'sl_{}'.format(scoretype)

path = os.path.join(path,scoretype)
if not os.path.exists(path):
    print("...making directory: ", path)
    os.makedirs(path)    
else:
    print("...directory exists: ", path)
    
    
data_labels = ['group_event_templates',
               'subj_event_templates',
               'loo_event_similarity_matrix', 
               'story_effect',
               'schema_effect']

perception_measures = [group, # (16,nVerts,4)
                       subj_templates, #(31,16,nVerts,4)
                       loo_ev_corr,  # (16,16,4,31) #N-1 spatial ISC 
                       story_effect, 
                       schema_effect]

fname = '{date}_{roi}_{roi_id:04d}_{hem}_{scoretype}.h5'.format(date=date, roi=roi, roi_id=roi_id,
                                                            hem=hem, scoretype=scoretype)
# fullpath = os.path.join(path, fname)
# print('...Saving to ', fullpath)

# with h5py.File(fullpath, 'w') as hf:

#     # create dict entry
#     hf = hf.create_group(hem)
    
#     # create sub-dict entries
#     for label,measure in zip(data_labels,perception_measures): 
#         hf.create_dataset(label, data=measure)
        
# print('...SAVING COMPLETE.')

1120 1089


1120 (1120,)



ValueError: could not broadcast input array from shape (1120,4) into shape (1089,4)

In [51]:
from tqdm import tqdm_notebook

In [8]:
subj_templates.shape

(31, 16, 324, 4)

In [13]:
np.isnan(subj_templates[2,:,:,0]).sum()

0

In [6]:
np.arange(4)[np.array((True, True, False, False))]

array([0, 1])

In [7]:
range(4)[np.array((True, True, False, False))]

TypeError: only integer scalar arrays can be converted to a scalar index

In [ ]:
percept['BigBang'][:,0,:].shape

In [ ]:
np.logical_and(roi_verts,np.all(~np.isnan(percept['BigBang'][:,0,:]),axis=1)).sum()

In [ ]:
ls ../../SchemaBigFiles/_PaperBigData

In [ ]:
pwd ..

In [ ]:
pwd ../..

In [ ]:
ls ../../

In [15]:
ls -1t /jukebox/norman/rmasis/clones/SchemaBigFiles/draft_PAPER/LOGS -n 5

ls: cannot access 5: No such file or directory
/jukebox/norman/rmasis/clones/SchemaBigFiles/draft_PAPER/LOGS:
total 54242320
-rw-rw-r--. 1 2057 360     447 Oct 14 15:43 slurm_-24409901.log
-rw-rw-r--. 1 2057 360     166 Oct 14 15:41 slurm_-24409900.log
-rw-rw-r--. 1 2057 360     181 Oct 14 15:40 slurm_-24409899.log
-rw-rw-r--. 1 2057 360 2368365 Oct  3 09:53 slurm_-24393186.log
-rw-rw-r--. 1 2057 360 2356012 Oct  3 09:53 slurm_-24393168.log
-rw-rw-r--. 1 2057 360 2345770 Oct  3 09:53 slurm_-24393184.log
-rw-rw-r--. 1 2057 360 2361348 Oct  3 09:53 slurm_-24393170.log
-rw-rw-r--. 1 2057 360 2353397 Oct  3 09:53 slurm_-24393180.log
-rw-rw-r--. 1 2057 360 2358889 Oct  3 09:53 slurm_-24393182.log
-rw-rw-r--. 1 2057 360 2341423 Oct  3 09:53 slurm_-24393174.log
-rw-rw-r--. 1 2057 360 2351215 Oct  3 09:53 slurm_-24393178.log
-rw-rw-r--. 1 2057 360 2384428 Oct  3 09:53 slurm_-24393172.log
-rw-rw-r--. 1 2057 360 2357780 Oct  3 09:53 slurm_-24393176.log
-rw-rw-r--. 1 2057 360 2356821 Oct  3 09:53

-rw-rw-r--. 1 2057 360 2367306 Oct  1 22:04 slurm_-24390324.log
-rw-rw-r--. 1 2057 360 2357114 Oct  1 22:04 slurm_-24390330.log
-rw-rw-r--. 1 2057 360 2344378 Oct  1 22:04 slurm_-24390390.log
-rw-rw-r--. 1 2057 360 2360030 Oct  1 22:04 slurm_-24390321.log
-rw-rw-r--. 1 2057 360 2368154 Oct  1 22:04 slurm_-24390387.log
-rw-rw-r--. 1 2057 360 2372136 Oct  1 22:04 slurm_-24390326.log
-rw-rw-r--. 1 2057 360 2366504 Oct  1 22:04 slurm_-24390333.log
-rw-rw-r--. 1 2057 360 2378633 Oct  1 22:04 slurm_-24390371.log
-rw-rw-r--. 1 2057 360 2361333 Oct  1 22:04 slurm_-24390363.log
-rw-rw-r--. 1 2057 360 2366152 Oct  1 22:04 slurm_-24390376.log
-rw-rw-r--. 1 2057 360 2365362 Oct  1 22:04 slurm_-24389862.log
-rw-rw-r--. 1 2057 360 2373471 Oct  1 22:04 slurm_-24390366.log
-rw-rw-r--. 1 2057 360 2357025 Oct  1 22:04 slurm_-24390365.log
-rw-rw-r--. 1 2057 360 2381124 Oct  1 22:04 slurm_-24390334.log
-rw-rw-r--. 1 2057 360 2378317 Oct  1 22:04 slurm_-24389858.log
-rw-rw-r--. 1 2057 360 2369988 Oct  1 22

-rw-rw-r--. 1 2057 360 2379321 Oct  1 22:01 slurm_-24387347.log
-rw-rw-r--. 1 2057 360 2357063 Oct  1 22:01 slurm_-24387371.log
-rw-rw-r--. 1 2057 360 2371416 Oct  1 22:01 slurm_-24387181.log
-rw-rw-r--. 1 2057 360 2383645 Oct  1 22:01 slurm_-24387441.log
-rw-rw-r--. 1 2057 360 2357173 Oct  1 22:01 slurm_-24387435.log
-rw-rw-r--. 1 2057 360 2367579 Oct  1 22:01 slurm_-24387447.log
-rw-rw-r--. 1 2057 360 2372557 Oct  1 22:01 slurm_-24387432.log
-rw-rw-r--. 1 2057 360 2384104 Oct  1 22:01 slurm_-24387452.log
-rw-rw-r--. 1 2057 360 2368623 Oct  1 22:01 slurm_-24387205.log
-rw-rw-r--. 1 2057 360 2378815 Oct  1 22:01 slurm_-24387434.log
-rw-rw-r--. 1 2057 360 2386639 Oct  1 22:01 slurm_-24387204.log
-rw-rw-r--. 1 2057 360 2383710 Oct  1 22:01 slurm_-24387834.log
-rw-rw-r--. 1 2057 360 2355238 Oct  1 22:01 slurm_-24387207.log
-rw-rw-r--. 1 2057 360 2382358 Oct  1 22:01 slurm_-24387749.log
-rw-rw-r--. 1 2057 360 2363643 Oct  1 22:01 slurm_-24387439.log
-rw-rw-r--. 1 2057 360 2371427 Oct  1 22

-rw-rw-r--. 1 2057 360 4697026 Oct  1 17:13 slurm_-24383722.log
-rw-rw-r--. 1 2057 360 4729922 Oct  1 17:13 slurm_-24383853.log
-rw-rw-r--. 1 2057 360 4708722 Oct  1 17:13 slurm_-24383850.log
-rw-rw-r--. 1 2057 360 4694770 Oct  1 17:13 slurm_-24383857.log
-rw-rw-r--. 1 2057 360 4701361 Oct  1 17:13 slurm_-24383848.log
-rw-rw-r--. 1 2057 360 4704290 Oct  1 17:13 slurm_-24383714.log
-rw-rw-r--. 1 2057 360 4706370 Oct  1 17:13 slurm_-24383715.log
-rw-rw-r--. 1 2057 360 4695197 Oct  1 17:12 slurm_-24383838.log
-rw-rw-r--. 1 2057 360 4708914 Oct  1 17:12 slurm_-24383865.log
-rw-rw-r--. 1 2057 360 4697634 Oct  1 17:12 slurm_-24383720.log
-rw-rw-r--. 1 2057 360 4718574 Oct  1 17:12 slurm_-24383852.log
-rw-rw-r--. 1 2057 360 4711202 Oct  1 17:12 slurm_-24383862.log
-rw-rw-r--. 1 2057 360 4700034 Oct  1 17:12 slurm_-24383851.log
-rw-rw-r--. 1 2057 360 4716002 Oct  1 17:12 slurm_-24383845.log
-rw-rw-r--. 1 2057 360 4697042 Oct  1 17:12 slurm_-24383841.log
-rw-rw-r--. 1 2057 360 4715902 Oct  1 17

-rw-rw-r--. 1 2057 360     326 Oct  1 15:03 slurm_-24378097.log
-rw-rw-r--. 1 2057 360     326 Oct  1 15:03 slurm_-24378095.log
-rw-rw-r--. 1 2057 360     326 Oct  1 15:03 slurm_-24378141.log
-rw-rw-r--. 1 2057 360     326 Oct  1 15:03 slurm_-24378101.log
-rw-rw-r--. 1 2057 360     326 Oct  1 15:03 slurm_-24378143.log
-rw-rw-r--. 1 2057 360     326 Oct  1 15:03 slurm_-24378140.log
-rw-rw-r--. 1 2057 360     326 Oct  1 15:03 slurm_-24378106.log
-rw-rw-r--. 1 2057 360     326 Oct  1 15:03 slurm_-24378109.log
-rw-rw-r--. 1 2057 360     326 Oct  1 15:03 slurm_-24378098.log
-rw-rw-r--. 1 2057 360     326 Oct  1 15:03 slurm_-24378085.log
-rw-rw-r--. 1 2057 360     326 Oct  1 15:03 slurm_-24378125.log
-rw-rw-r--. 1 2057 360     326 Oct  1 15:03 slurm_-24378100.log
-rw-rw-r--. 1 2057 360     326 Oct  1 15:03 slurm_-24378123.log
-rw-rw-r--. 1 2057 360     326 Oct  1 15:03 slurm_-24378127.log
-rw-rw-r--. 1 2057 360     326 Oct  1 15:03 slurm_-24378108.log
-rw-rw-r--. 1 2057 360     326 Oct  1 15

-rw-rw-r--. 1 2057 360 2381877 Oct  1 11:16 slurm_-24373141.log
-rw-rw-r--. 1 2057 360 2360709 Oct  1 11:16 slurm_-24373143.log
-rw-rw-r--. 1 2057 360 2370207 Oct  1 11:16 slurm_-24373104.log
-rw-rw-r--. 1 2057 360 2379812 Oct  1 11:16 slurm_-24373167.log
-rw-rw-r--. 1 2057 360 2375752 Oct  1 11:16 slurm_-24373062.log
-rw-rw-r--. 1 2057 360 2353341 Oct  1 11:16 slurm_-24373114.log
-rw-rw-r--. 1 2057 360 2377567 Oct  1 11:16 slurm_-24373061.log
-rw-rw-r--. 1 2057 360 2356383 Oct  1 11:16 slurm_-24373140.log
-rw-rw-r--. 1 2057 360 2380952 Oct  1 11:16 slurm_-24373106.log
-rw-rw-r--. 1 2057 360 2352380 Oct  1 11:16 slurm_-24372407.log
-rw-rw-r--. 1 2057 360 2377388 Oct  1 11:16 slurm_-24373156.log
-rw-rw-r--. 1 2057 360 2369695 Oct  1 11:16 slurm_-24372799.log
-rw-rw-r--. 1 2057 360 2377312 Oct  1 11:16 slurm_-24372803.log
-rw-rw-r--. 1 2057 360 2380597 Oct  1 11:16 slurm_-24372864.log
-rw-rw-r--. 1 2057 360 2349538 Oct  1 11:16 slurm_-24372281.log
-rw-rw-r--. 1 2057 360 2377449 Oct  1 11

In [16]:
cat /jukebox/norman/rmasis/clones/SchemaBigFiles/draft_PAPER/LOGS/slurm_-24409901.log

DATE LABEL 20211014
HEM L
ROI SL
ROI_ID 1
SCORETYPE sl_percept_score
331 331
Traceback (most recent call last):
  File "01_PerceptionStorySchema_step2.py", line 273, in <module>
    group, subj_templates, loo_ev_corr = RunPerceptionSimilarityMatrix(roi_verts,percept,hem)
  File "01_PerceptionStorySchema_step2.py", line 84, in RunPerceptionSimilarityMatrix
    for s in tqdm_notebook(range(nSubj)):
NameError: name 'tqdm_notebook' is not defined


# RECALL 

In [4]:
from _functions import * #includes constants and score function
import os
import deepdish as dd

# from util import * #utility stuff
from _deconvolve import * #utility stuff

import brainiak.eventseg.event as event #HMM

import numpy as np #used a lot

import h5py #for saving final output

import sys 


################
################ INPUTS
################

date = 20211014
hem = 'R'
roi = 'SL'
roi_id = 22
scoretype = 'sl_recall_score'
modality_mode = 'within_modality'

# date = sys.argv[1] # 'date label to use'
# hem = str(sys.argv[2]) # 'L' or 'R'
# roi = sys.argv[3] # 'STS', 'SL', 'atlas'
# roi_id = int(sys.argv[4]) # "9999" or int
# scoretype = sys.argv[5] # "'sl_recall_score'" or any directory name that makes sense
# modality_mode = str(sys.argv[6]) #within_modality or across_modality

################
################ CONSTANTS & DESIGN MATRIX
################

stories = ['Brazil',  'Derek', 'MrBean',   'PulpFiction',
           'BigBang', 'Santa', 'Shame',    'Vinny',
           'DueDate', 'GLC',   'KandD',    'Nonstop',
           'Friends', 'HIMYM', 'Seinfeld', 'UpInTheAir']

nSubj = 30 # lost recall data to subject 31 due to signal loss
TR = 1.5
nStories = len(stories)
nEvents = 4
nPerm = 1000
nv = 40962

# Story event boundaries (in seconds)
events_seconds_intact = np.array([
     [0,     6,    46,    73,   115,   184],
     [0,     6,    30,   111,   169,   188],
     [0,     6,    21,    74,   159,   186],
     [0,     6,    40,    56,   171,   185],
     [0,     6,    31,    46,   156,   171],
     [0,     6,    71,   104,   165,   175],
     [0,     6,    26,    94,   134,   175],
     [0,     6,    28,    59,   151,   179],
     [0,     6,    51,   111,   122,   189],
     [0,     6,    23,    70,    84,   171],
     [0,     6,    53,    82,   136,   184],
     [0,     6,    29,    77,   123,   190],
     [0,     6,    30,    97,   138,   163],
     [0,     6,    36,   109,   124,   169],
     [0,     6,    39,    85,   107,   173],
     [0,     6,    33,   108,   144,   187]])

# Story lengths (in TRs)
story_TRs = np.array([124, 126, 125, 124,
                      115, 118, 118, 120,
                      127, 115, 124, 128,
                      110, 114, 116, 126])


# Compute design matrices for all stories
design_intact = []
for i in range(len(stories)):
    subevent_E = np.zeros((events_seconds_intact[i, 5], 5))
    for e in range(5):
        subevent_E[events_seconds_intact[i, e]:
                   (events_seconds_intact[i, e + 1] + 1), e] = 1
    design_intact.append(regressor_to_TR(subevent_E[:,:], TR, story_TRs[i]))
design_intact = np.array(design_intact)


################
################ FUNCTIONS 
################



################
################ RUN ANALYSIS
################

braindata_path = '../../SchemaBigFiles/FullPerceptRecall'

## load recall timeseries
if 'hipp' in roi:
    hipp_recall = dd.io.load(os.path.join(braindata_path,"hipp_perception_recall.h5"))
    recall = hipp_recall['recall']
else:
    recall = dd.io.load(os.path.join(braindata_path,'wholebrain_recall.h5'),'/'+hem)

### load perception templates
percept_dirname = '{}_percept_score'.format(scoretype.split('_')[0].lower())
path = '../../SchemaBigFiles/_PaperOutputData/{}'.format(percept_dirname)
fname = '{date}_{roi}_{roi_id:04d}_{hem}_{percept_dirname}.h5'.format(date=date, roi=roi, roi_id=roi_id,
                                                            hem=hem, percept_dirname=percept_dirname)
fullpath = os.path.join(path, fname)
story_templates = dd.io.load(fullpath, '/' + hem + '/' + 'group_event_templates')
# story_templates = dd.io.load(fullpath, '/' + hem + '/' + 'subj_event_templates') #for individual subject analysis, i think.

## load ROI verts
roi_verts = ExtractROI(roi, roi_id, hem)



In [22]:
### RUN HMM FITTING PROCEDURE
dim = roi_verts.sum()
print(dim)

template_match = np.zeros((nStories, nStories, 4, nSubj))
hmm_overall_match = np.zeros((nStories,nStories,nSubj))

## iterate through every subject
for s,subj in enumerate((subjects)):
    
    ## iterate through story to use as template
    for st, story in enumerate(stories):
        
        template = story_templates[st,:,:] #template from perception
#         template = story_templates[s,st,:,:] #for individual subjects, dimension mismatch
        
        nTRs = recall[story][str(s)].shape[1] #total TRs in timeseries of this story's recall
        
        ## declare HMM object
        ev = event.EventSegment(nEvents) #each story has 4 schematic subevents

#         ## grab perception timeseries of current subject to calculate variance parameter 
#         ## (there could be nan vertices for a particular story for a particular subject for specified ROI)
#         percept = dd.io.load(os.path.join(braindata_path,'wholebrain_perception.h5'),'/'+hem+'/'+ story, 
#                       dd.aslice[np.where(roi_verts)[0],:,s], unpack=True)
        
        ## grab perception timeseries of current subject to calculate variance parameter 
        ## (there could be nan vertices for a particular story for a particular subject for specified ROI)
        if 'hippo' not in roi:
            percept = dd.io.load(os.path.join(braindata_path,'wholebrain_perception.h5'),'/'+hem+'/'+ story, 
                          dd.aslice[np.where(roi_verts)[0],:,:], unpack=True)[:,:,has_R][:,:,s]
        else:
            percept = dd.io.load(os.path.join(braindata_path,"hipp_perception.h5"), '/' + story,
                                 dd.aslice[np.where(roi_verts)[0],:,:], unpack=True)[:,:,has_R][:,:,s]
        
        print(template.shape, percept.shape)

        ### !! COMBACK AND REVISIT; less precise b/c we haven't found out whether recall timeseries has same valid verts
        valid_verts = ~np.isnan(percept[:,0]) * ~np.isnan(template[:,0])
        ev_var1 = ev.calc_weighted_event_var(percept[valid_verts].T, design_intact[st][:,1:], template[valid_verts,:])
        
#         print(subj, np.any(np.isnan(percept)),np.any(np.isnan(template)),np.all(np.isnan(percept)),np.all(np.isnan(template)), ev_var1)

        ## iterate through story to fit with template
        for st_j, story_j in enumerate(stories):

            recall_timeseries = recall[story_j][str(s)][roi_verts] 
            
            valid_verts = ~np.isnan(percept[:,0]) * ~np.isnan(template[:,0]) * ~np.isnan(recall_timeseries[:,0])

            ev.set_event_patterns(template[valid_verts]) #provide HMM with story template of shape: (voxel,event)

            ### !!!!!!!!!!!
            ### !! COME BACK REVISIT; more precise b/cj we are using non nans in both percept and recall timeseries
            ev_var = ev.calc_weighted_event_var(percept[valid_verts].T, design_intact[st][:,1:], template[valid_verts])
            print('... ', ev_var1==ev_var)
            print(ev_var)
#             print(recall_timeseries[valid_verts].T)
            
            
            ev_fit = ev.find_events(recall_timeseries[valid_verts].T, var=ev_var)[0] ## this fixes the problem of not finding events per subject!

            #plt.figure()
            #plt.plot(ev_fit); plt.title(stories[story_j])
            #labels = np.argmax(ev_fit, axis=1) 
            #bounds = np.where(np.diff(labels))[0]
            #bounds_aug = np.concatenate(([0],bounds,[nTRs]))

            weighted_vox = np.matmul(recall_timeseries[valid_verts],ev_fit) #(voxel x time) * (time, event) --> (voxel x event)

            ###
            ### SCORING FOR HMM IN HOW WELL IT DID AT MATCHING PERCEPTION TO RECALL FOR THIS STORY
            ###

            #events.T = (4,nVox), weighted_vox.T = (nVox, 4)
            cc = np.corrcoef(template[valid_verts].T, weighted_vox.T)[:nEvents, nEvents:] # the .T gives us both --> (nVox,events) and (events,vox)
            print(np.isnan(weighted_vox.ravel()).sum(), np.isnan(template[valid_verts].ravel()).sum(),
                 np.isnan(cc.ravel()).sum())
            ### SYMMETRIC template match score
            for i in range(nEvents):
                template_match[st,st_j,i,s] = cc[i,i] - np.nanmean(cc[i,np.arange(nEvents)!=i],axis=0)/2 - np.nanmean(cc[np.arange(nEvents)!=i,i],axis=0)/2 

            print('TEMPLATE match: ', np.isnan(template_match[st,st_j,i,s]))
            ### OLD WAY TO CALCULATE template match
            d = np.diag(cc).sum()
            calc = d/nEvents - (cc.sum()-d)/(nEvents**2 - nEvents) #diagonal_mean minus off-diagonal_mean
            hmm_overall_match[st,st_j,s] = calc #the score of this hmm at trying to match perception to recall


            #vartup =tuple(['{:.3f}'.format(ev_var[i]) for i in range(len(ev_var))])
            #plt.figure();plt.imshow(cc);plt.colorbar();plt.title('score: {:.3f},subj: {},st: {}\n var:{}'.format(calc, subj,stories[story],vartup))
            #plt.figure();plt.imshow(cc);plt.colorbar();plt.title('score: {:.3f},subj: {},st: {}\n'.format(calc, subj,stories[story]))
            #plt.show()
            
            
            


324
(324, 4) (324, 124)
...  [ True  True  True  True]
[1.9294397  2.17163592 1.98247111 1.99278766]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[1.9294397  2.17163592 1.98247111 1.99278766]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[1.9294397  2.17163592 1.98247111 1.99278766]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[1.9294397  2.17163592 1.98247111 1.99278766]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[1.9294397  2.17163592 1.98247111 1.99278766]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[1.9294397  2.17163592 1.98247111 1.99278766]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[1.9294397  2.17163592 1.98247111 1.99278766]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[1.9294397  2.17163592 1.98247111 1.99278766]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[1.9294397  2.17163592 1.98247111 1.99278766]
0 0 0
TEMPLATE match:  False
...  [ True  True  Tru

(324, 4) (324, 118)
...  [ True  True  True  True]
[2.04408623 2.02365793 2.15357808 2.43163752]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.04408623 2.02365793 2.15357808 2.43163752]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.04408623 2.02365793 2.15357808 2.43163752]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.04408623 2.02365793 2.15357808 2.43163752]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.04408623 2.02365793 2.15357808 2.43163752]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.04408623 2.02365793 2.15357808 2.43163752]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.04408623 2.02365793 2.15357808 2.43163752]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.04408623 2.02365793 2.15357808 2.43163752]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.04408623 2.02365793 2.15357808 2.43163752]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  T

(324, 4) (324, 124)
...  [ True  True  True  True]
[2.09073981 2.10700589 2.08659189 2.06230635]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.09073981 2.10700589 2.08659189 2.06230635]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.09073981 2.10700589 2.08659189 2.06230635]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.09073981 2.10700589 2.08659189 2.06230635]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.09073981 2.10700589 2.08659189 2.06230635]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.09073981 2.10700589 2.08659189 2.06230635]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.09073981 2.10700589 2.08659189 2.06230635]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.09073981 2.10700589 2.08659189 2.06230635]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.09073981 2.10700589 2.08659189 2.06230635]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  T

(324, 4) (324, 126)
...  [ True  True  True  True]
[2.01713958 2.02031129 2.08903784 2.10464157]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.01713958 2.02031129 2.08903784 2.10464157]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.01713958 2.02031129 2.08903784 2.10464157]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.01713958 2.02031129 2.08903784 2.10464157]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.01713958 2.02031129 2.08903784 2.10464157]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.01713958 2.02031129 2.08903784 2.10464157]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.01713958 2.02031129 2.08903784 2.10464157]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.01713958 2.02031129 2.08903784 2.10464157]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.01713958 2.02031129 2.08903784 2.10464157]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  T

(324, 4) (324, 115)
...  [ True  True  True  True]
[2.10028926 2.11904549 2.016369   2.24169585]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.10028926 2.11904549 2.016369   2.24169585]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.10028926 2.11904549 2.016369   2.24169585]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.10028926 2.11904549 2.016369   2.24169585]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.10028926 2.11904549 2.016369   2.24169585]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.10028926 2.11904549 2.016369   2.24169585]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.10028926 2.11904549 2.016369   2.24169585]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.10028926 2.11904549 2.016369   2.24169585]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.10028926 2.11904549 2.016369   2.24169585]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  T

...

0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.24705831 2.06761606 2.13571385 2.05495459]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.24705831 2.06761606 2.13571385 2.05495459]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.24705831 2.06761606 2.13571385 2.05495459]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.24705831 2.06761606 2.13571385 2.05495459]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.24705831 2.06761606 2.13571385 2.05495459]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.24705831 2.06761606 2.13571385 2.05495459]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.24705831 2.06761606 2.13571385 2.05495459]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.24705831 2.06761606 2.13571385 2.05495459]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.24705831 2.06761606 2.13571385 2.05495459]
0 0 0
TEMPLATE match:  False
...  [ True  True

0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.1032996  2.01846772 2.06180041 2.04109275]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.1032996  2.01846772 2.06180041 2.04109275]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.1032996  2.01846772 2.06180041 2.04109275]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.1032996  2.01846772 2.06180041 2.04109275]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.1032996  2.01846772 2.06180041 2.04109275]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.1032996  2.01846772 2.06180041 2.04109275]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.1032996  2.01846772 2.06180041 2.04109275]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.1032996  2.01846772 2.06180041 2.04109275]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.1032996  2.01846772 2.06180041 2.04109275]
0 0 0
TEMPLATE match:  False
...  [ True  True

0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.03460602 2.20857771 2.03241034 2.34311858]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.03460602 2.20857771 2.03241034 2.34311858]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.03460602 2.20857771 2.03241034 2.34311858]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.03460602 2.20857771 2.03241034 2.34311858]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.03460602 2.20857771 2.03241034 2.34311858]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.03460602 2.20857771 2.03241034 2.34311858]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.03460602 2.20857771 2.03241034 2.34311858]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.03460602 2.20857771 2.03241034 2.34311858]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.03460602 2.20857771 2.03241034 2.34311858]
0 0 0
TEMPLATE match:  False
...  [ True  True

(324, 4) (324, 124)
...  [ True  True  True  True]
[2.05902734 2.21915498 2.15911164 2.09712777]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.05902734 2.21915498 2.15911164 2.09712777]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.05902734 2.21915498 2.15911164 2.09712777]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.05902734 2.21915498 2.15911164 2.09712777]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.05902734 2.21915498 2.15911164 2.09712777]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.05902734 2.21915498 2.15911164 2.09712777]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.05902734 2.21915498 2.15911164 2.09712777]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.05902734 2.21915498 2.15911164 2.09712777]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.05902734 2.21915498 2.15911164 2.09712777]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  T

...  [ True  True  True  True]
[2.16843112 2.03142106 2.06827844 2.10846701]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.16843112 2.03142106 2.06827844 2.10846701]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.16843112 2.03142106 2.06827844 2.10846701]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.16843112 2.03142106 2.06827844 2.10846701]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.16843112 2.03142106 2.06827844 2.10846701]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.16843112 2.03142106 2.06827844 2.10846701]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.16843112 2.03142106 2.06827844 2.10846701]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.16843112 2.03142106 2.06827844 2.10846701]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.16843112 2.03142106 2.06827844 2.10846701]
0 0 0
TEMPLATE match:  False
...  [ True  True  True  True]
[2.16843112 2.0

In [21]:
dd.io.load(os.path.join(braindata_path,"hipp_perception.h5"), '/' + story,
                                 dd.aslice[:,:,:]).shape

(1289, 124, 31)

In [17]:
percept.shape

(324, 124, 31)

In [23]:
## get story and schema scores for every event
story_effect = np.zeros((nSubj,nStories,nEvents,nPerm+1)) 
schema_effect = np.zeros((nSubj,nStories,nEvents,nPerm+1)) 

for ev in range(nEvents):
    story_effect[:,:,ev,:], schema_effect[:,:,ev,:] = GetStorySchemaEffect(template_match[:,:,ev,:], test_mod=modality_mode)
    
    
################
################ SAVE DATA
################

path = '../../SchemaBigFiles/_PaperOutputData'

path = os.path.join(path,scoretype)
if not os.path.exists(path):
    print("...making directory: ", path)
    os.makedirs(path)    
else:
    print("...directory exists: ", path)

fname = '{date}_{roi}_{roi_id:04d}_{hem}_{scoretype}.h5'.format(date=date, roi=roi, roi_id=roi_id,
                                                            hem=hem, scoretype=scoretype)
fullpath = os.path.join(path, fname)

print('...Saving to ', fullpath)

data_labels = ['reinstatement_similarity_matrix',
              'story_effect',
              'schema_effect']

reinstatement_measures = [template_match, # nStories, nStories, 4, nSubj
                         story_effect, # (30,16,4,1001)
                         schema_effect] # (30,16,4,1001)

with h5py.File(fullpath, 'w') as hf:

    # create dict entry
    hf = hf.create_group(hem)
    
    # create sub-dict entries
    for label,measure in zip(data_labels,reinstatement_measures): 
        hf.create_dataset(label, data=measure)
        
print('...SAVING COMPLETE.')

...making directory:  ../../SchemaBigFiles/_PaperOutputData/sl_recall_scores
...Saving to  ../../SchemaBigFiles/_PaperOutputData/sl_recall_scores/20211014_SL_0022_R_sl_recall_scores.h5
...SAVING COMPLETE.


# WITHIN SUBJ RECALL

In [7]:
from _functions import * #includes constants and score function
import os
import deepdish as dd

# from util import * #utility stuff
from _deconvolve import * #utility stuff

import brainiak.eventseg.event as event #HMM

import numpy as np #used a lot

import h5py #for saving final output

import sys 


date = 20211014 #sys.argv[1] # 'date label to use'
hem = 'L' #str(sys.argv[2]) # 'L' or 'R'
roi = 'mPFC' #sys.argv[3] # 'STS', 'SL', 'atlas'
roi_id = 9999 #int(sys.argv[4]) # "9999" or int
scoretype = 'roi_recall_score' #sys.argv[5] # "sl_percept_scores" or any directory name that makes sense
extra = 'within_modality' #sys.argv[6] #within_modality


### load perception templates
percept_dirname = '{}_percept_score'.format(scoretype.split('_')[0].lower())
# path = '../SchemaBigFiles/draft_PAPER/{}'.format(percept_dirname)
path = '../../SchemaBigFiles/_PaperOutputData/{}'.format(percept_dirname)

fname = '{date}_{roi}_{roi_id:04d}_{hem}_{percept_dirname}_{extra}.h5'.format(date=date, roi=roi, roi_id=roi_id,
                                                            hem=hem, percept_dirname=percept_dirname,extra=extra)
fullpath = os.path.join(path, fname)
# story_templates = dd.io.load(fullpath, '/' + hem + '/' + 'group_event_templates')
story_templates = dd.io.load(fullpath, '/' + hem + '/' + 'subj_event_templates')[has_R,:,:,:] #for individual subject analysis, i think.
#for individual subject analysis, i think.


In [6]:
x = dd.io.load(fullpath, '/' + hem)
x.keys()

dict_keys(['loo_event_similarity_matrix', 'schema_effect', 'story_effect'])

In [15]:
from _functions import * #includes constants and score function
import os
import deepdish as dd

# from util import * #utility stuff
from _deconvolve import * #utility stuff

import brainiak.eventseg.event as event #HMM

import numpy as np #used a lot

import h5py #for saving final output

import sys 

import time

######################################################### COMPARE THIS TO THE RECALL UPDATE FOR VALID VERTS CHECKS AND STUFF

################
################ INPUTS
################

# date = sys.argv[1] # 'date label to use'
# hem = str(sys.argv[2]) # 'L' or 'R'
# roi = sys.argv[3] # 'STS', 'SL', 'atlas'
# roi_id = int(sys.argv[4]) # "9999" or int
# scoretype = sys.argv[5] # "sl_percept_scores" or any directory name that makes sense
# extra = sys.argv[6] #within_modality

date = 20211014 #sys.argv[1] # 'date label to use'
hem = 'R' #sys.argv[2] # 'L' or 'R'
roi = 'SL' #sys.argv[3] # 'STS', 'SL', 'atlas'
roi_id = 22 #int(sys.argv[4]) # "9999" or int
scoretype = 'sl_recall_score' #sys.argv[5] # "sl_percept_scores" or any directory name that makes sense
extra = 'within_modality'

################
################ CONSTANTS & DESIGN MATRIX
################

stories = ['Brazil',  'Derek', 'MrBean',   'PulpFiction',
           'BigBang', 'Santa', 'Shame',    'Vinny',
           'DueDate', 'GLC',   'KandD',    'Nonstop',
           'Friends', 'HIMYM', 'Seinfeld', 'UpInTheAir']

nSubj = 30 # lost recall data to subject 31 due to signal loss
TR = 1.5
nStories = len(stories)
nEvents = 4
nPerm = 1000
nv = 40962

# Story event boundaries (in seconds)
events_seconds_intact = np.array([
     [0,     6,    46,    73,   115,   184],
     [0,     6,    30,   111,   169,   188],
     [0,     6,    21,    74,   159,   186],
     [0,     6,    40,    56,   171,   185],
     [0,     6,    31,    46,   156,   171],
     [0,     6,    71,   104,   165,   175],
     [0,     6,    26,    94,   134,   175],
     [0,     6,    28,    59,   151,   179],
     [0,     6,    51,   111,   122,   189],
     [0,     6,    23,    70,    84,   171],
     [0,     6,    53,    82,   136,   184],
     [0,     6,    29,    77,   123,   190],
     [0,     6,    30,    97,   138,   163],
     [0,     6,    36,   109,   124,   169],
     [0,     6,    39,    85,   107,   173],
     [0,     6,    33,   108,   144,   187]])

# Story lengths (in TRs)
story_TRs = np.array([124, 126, 125, 124,
                      115, 118, 118, 120,
                      127, 115, 124, 128,
                      110, 114, 116, 126])


# Compute design matrices for all stories
design_intact = []
for i in range(len(stories)):
    subevent_E = np.zeros((events_seconds_intact[i, 5], 5))
    for e in range(5):
        subevent_E[events_seconds_intact[i, e]:
                   (events_seconds_intact[i, e + 1] + 1), e] = 1
    design_intact.append(regressor_to_TR(subevent_E[:,:], TR, story_TRs[i]))
design_intact = np.array(design_intact)


################
################ FUNCTIONS 
################

# def ExtractROI():
#     '''
#     roi is string with "SL", "atlas", or specific ROI like "PMC".
#     roi_id is integer for index to go through. for searchlights this can range from 0-1000+
#     while for the atlas this will range from 0-180
#     '''

#     nv = 40962
#     roi_verts = np.zeros((nv),dtype=bool) #create full hemisphere

#     hemi = 'left' if hem == 'L' else 'right'

#     roi_path = '/jukebox/norman/rmasis/clones/SchemaBigFiles/draft_PAPER/ROIs'

#     if roi == 'SL':
#         SL_indeces = dd.io.load(os.path.join(roi_path,'SLlist_c10.h5'), '/'+ hem )[roi_id]
#         roi_verts[SL_indeces] = True

#     elif roi == 'atlas':
#         atlas = {}
#         atlas[hem] = read_gifti(os.path.join(roi_path,'{}h.HCP-MMP1.fsaverage6.gii'.format(hem.lower())))[0] 
#         roi_indeces = np.where(atlas[hem] == roi_id)[0]
#         roi_verts[roi_indeces] = True

#     else: #for specific ROIs like "PMC", "mPFC", or networks like 'MTN'
#         verts = dd.io.load(os.path.join(roi_path,'{}_verts.h5'.format(roi)))
#         roi_verts[verts[hemi]] = True
        
#     return roi_verts


# def ExtractROI():
#     '''
#     roi is string with "SL", "atlas", or specific ROI like "PMC".
#     roi_id is integer for index to go through. for searchlights this can range from 0-1000+
#     while for the atlas this will range from 0-180
#     '''

#     nv = 40962
#     roi_verts = np.zeros((nv),dtype=bool) #create full hemisphere

#     hemi = 'left' if hem == 'L' else 'None' if hem == 'None' else 'right'

#     roi_path = '/jukebox/norman/rmasis/clones/SchemaBigFiles/draft_PAPER/ROIs'

#     if roi == 'SL':
#         SL_indeces = dd.io.load(os.path.join(roi_path,'SLlist_c10.h5'), '/'+ hem )[roi_id]
#         roi_verts[SL_indeces] = True

#     elif roi == 'atlas':
#         atlas = {}
#         atlas[hem] = read_gifti(os.path.join(roi_path,'{}h.HCP-MMP1.fsaverage6.gii'.format(hem.lower())))[0] 
#         roi_indeces = np.where(atlas[hem] == roi_id)[0]
#         roi_verts[roi_indeces] = True

#     else: #for specific ROIs like "PMC", "mPFC", or networks like 'MTN'
        
#         if 'hippo' not in roi: #for all OTHER ROIs
#             verts = dd.io.load(os.path.join(roi_path,'{}_verts.h5'.format(roi))) 
#             roi_verts[verts[hemi]] = True
#         else: #for hippo
#             roi_verts = np.zeros((1289),dtype=bool)
#             if roi == 'hippo':
#                 roi_verts = np.full(1289, fill_value=True) ##i know how many voxels in hippo
#             elif roi =='ahippo':
#                 verts = dd.io.load(os.path.join(roi_path,'{}_verts.h5'.format('hippo')))['ahippo']
#                 roi_verts[verts] = True
#             elif roi == 'phippo':
#                 verts = dd.io.load(os.path.join(roi_path,'{}_verts.h5'.format('hippo')))['phippo']
#                 roi_verts[verts] = True
        
#     return roi_verts

################
################ RUN ANALYSIS
################

start_time = time.time()

## load ROI verts
roi_verts = ExtractROI(roi, roi_id, hem)

###
####### GET GENERAL VALID VERTS (20210913
###

# braindata_path = '/jukebox/norman/rmasis/clones/SchemaBigFiles/FullPerceptRecall'
braindata_path = '../../SchemaBigFiles/FullPerceptRecall'


if 'hippo' not in roi:
    percept = dd.io.load(os.path.join(braindata_path,'wholebrain_perception.h5'),'/'+hem) 
else:
    percept = dd.io.load(os.path.join(braindata_path,"hipp_perception.h5"))
      
# percept = dd.io.load(os.path.join(braindata_path,'wholebrain_perception.h5'),'/'+hem) 

gen_valid_verts = roi_verts.copy()
for story in stories:
    gen_valid_verts = gen_valid_verts * ~np.any(np.any(np.isnan(percept[story]), axis=2), axis=1)
del(percept) #don't need it after getting valid verts
    
    
## load recall timeseries
if 'hipp' in roi:
    recall = dd.io.load(os.path.join(braindata_path,"hipp_perception_recall.h5"))['recall']
else:
    recall = dd.io.load(os.path.join(braindata_path,'wholebrain_recall.h5'),'/'+hem)

### load perception templates (for within subjects HMM fitting)
percept_dirname = '{}_percept_score'.format(scoretype.split('_')[0].lower())
# path = '../SchemaBigFiles/draft_PAPER/{}'.format(percept_dirname)
path = '../../SchemaBigFiles/_PaperOutputData/{}'.format(percept_dirname)

fname = '{date}_{roi}_{roi_id:04d}_{hem}_{percept_dirname}_{extra}.h5'.format(date=date, roi=roi, roi_id=roi_id,
                                                            hem=hem, percept_dirname=percept_dirname,extra=extra)
fullpath = os.path.join(path, fname)
# story_templates = dd.io.load(fullpath, '/' + hem + '/' + 'group_event_templates')
story_templates = dd.io.load(fullpath, '/' + hem + '/' + 'subj_event_templates')[has_R,:,:,:] #for individual subject analysis, i think.
#for individual subject analysis, i think.


### RUN HMM FITTING PROCEDURE
dim = roi_verts.sum()
print(dim)


template_match = np.zeros((nStories, nStories, 4, nSubj))
hmm_overall_match = np.zeros((nStories,nStories,nSubj))

## iterate through every subject
for s,subj in enumerate((subjects)):
    
    ## iterate through story to use as template
    for st, story in enumerate(stories):
        
#         template = story_templates[st,:,:] #template from perception
        template = story_templates[s,st,:,:] #for individual subjects, dimension mismatch
        
        nTRs = recall[story][str(s)].shape[1] #total TRs in timeseries of this story's recall
        
        ## declare HMM object
        ev = event.EventSegment(nEvents) #each story has 4 schematic subevents

        ## grab perception timeseries of current subject to calculate variance parameter 
        ## (there could be nan vertices for a particular story for a particular subject for specified ROI)
#         percept = dd.io.load(os.path.join(braindata_path,'wholebrain_perception.h5'),'/'+hem+'/'+ story, 
#                       dd.aslice[np.where(roi_verts)[0],:,s], unpack=True)

        ## grab perception timeseries of current subject to calculate variance parameter 
        ## (there could be nan vertices for a particular story for a particular subject for specified ROI)
        if 'hippo' not in roi:
#             percept = dd.io.load(os.path.join(braindata_path,'wholebrain_perception.h5'),'/'+hem+'/'+ story, 
#                           dd.aslice[np.where(gen_valid_verts)[0],:,:], unpack=True)[:,:,has_R][:,:,s]
            percept = dd.io.load(os.path.join(braindata_path,'wholebrain_perception.h5'),'/'+hem+'/'+ story, 
                          dd.aslice[np.where(roi_verts)[0],:,:], unpack=True)[:,:,has_R][:,:,s]
        else:
#             percept = dd.io.load(os.path.join(braindata_path,"hipp_perception.h5"), '/' + story,
#                                  dd.aslice[np.where(gen_valid_verts)[0],:,:], unpack=True)[:,:,has_R][:,:,s]
            percept = dd.io.load(os.path.join(braindata_path,"hipp_perception.h5"), '/' + story,
                                 dd.aslice[np.where(roi_verts)[0],:,:], unpack=True)[:,:,has_R][:,:,s]
        
        print(template.shape, percept.shape)

        ### !! COMBACK AND REVISIT; less precise b/c we haven't found out whether recall timeseries has same valid verts
        valid_verts = ~np.isnan(percept[:,0]) * ~np.isnan(template[:,0])
        ev_var1 = ev.calc_weighted_event_var(percept[valid_verts].T, design_intact[st][:,1:], template[valid_verts,:])
        print("VALID VERTS 1: ", valid_verts.sum())
#         print(subj, np.any(np.isnan(percept)),np.any(np.isnan(template)),np.all(np.isnan(percept)),np.all(np.isnan(template)), ev_var1)

        ## iterate through story to fit with template
        for st_j, story_j in enumerate(stories):

            recall_timeseries = recall[story_j][str(s)][roi_verts] 
#             recall_timeseries = recall[story_j][str(s)][gen_valid_verts] 
            
            valid_verts = ~np.isnan(percept[:,0]) * ~np.isnan(template[:,0]) * ~np.isnan(recall_timeseries[:,0])
            print("VALID VERTS 2: ", valid_verts.sum())

            ev.set_event_patterns(template[valid_verts]) #provide HMM with story template of shape: (voxel,event)

            ### !!!!!!!!!!!
            ### !! COME BACK REVISIT; more precise b/cj we are using non nans in both percept and recall timeseries
            ev_var = ev.calc_weighted_event_var(percept[valid_verts].T, design_intact[st][:,1:], template[valid_verts])
            print('... ', ev_var1==ev_var)
            print(ev_var)
            print(recall_timeseries[valid_verts].T)
            
            
            ev_fit = ev.find_events(recall_timeseries[valid_verts].T, var=ev_var)[0] ## this fixes the problem of not finding events per subject!

            #plt.figure()
            #plt.plot(ev_fit); plt.title(stories[story_j])
            #labels = np.argmax(ev_fit, axis=1) 
            #bounds = np.where(np.diff(labels))[0]
            #bounds_aug = np.concatenate(([0],bounds,[nTRs]))

            weighted_vox = np.matmul(recall_timeseries[valid_verts],ev_fit) #(voxel x time) * (time, event) --> (voxel x event)

            ###
            ### SCORING FOR HMM IN HOW WELL IT DID AT MATCHING PERCEPTION TO RECALL FOR THIS STORY
            ###

            #events.T = (4,nVox), weighted_vox.T = (nVox, 4)
            cc = np.corrcoef(template[valid_verts].T, weighted_vox.T)[:nEvents, nEvents:] # the .T gives us both --> (nVox,events) and (events,vox)
            print(np.isnan(weighted_vox.ravel()).sum(), np.isnan(template[valid_verts].ravel()).sum(),
                 np.isnan(cc.ravel()).sum())
            ### SYMMETRIC template match score
            for i in range(nEvents):
                template_match[st,st_j,i,s] = cc[i,i] - np.nanmean(cc[i,np.arange(nEvents)!=i],axis=0)/2 - np.nanmean(cc[np.arange(nEvents)!=i,i],axis=0)/2 

            print('TEMPLATE match: ', np.isnan(template_match[st,st_j,i,s]))
            ### OLD WAY TO CALCULATE template match
            d = np.diag(cc).sum()
            calc = d/nEvents - (cc.sum()-d)/(nEvents**2 - nEvents) #diagonal_mean minus off-diagonal_mean
            hmm_overall_match[st,st_j,s] = calc #the score of this hmm at trying to match perception to recall


            #vartup =tuple(['{:.3f}'.format(ev_var[i]) for i in range(len(ev_var))])
            #plt.figure();plt.imshow(cc);plt.colorbar();plt.title('score: {:.3f},subj: {},st: {}\n var:{}'.format(calc, subj,stories[story],vartup))
            #plt.figure();plt.imshow(cc);plt.colorbar();plt.title('score: {:.3f},subj: {},st: {}\n'.format(calc, subj,stories[story]))
            #plt.show()
            
            
            
## get story and schema scores for every event
story_effect = np.zeros((nSubj,nStories,nEvents,nPerm+1)) 
schema_effect = np.zeros((nSubj,nStories,nEvents,nPerm+1)) 

for ev in range(nEvents):
    story_effect[:,:,ev,:], schema_effect[:,:,ev,:] = GetStorySchemaEffect(template_match[:,:,ev,:])
    

################
################ SAVE DATA
################

# path = '../SchemaBigFiles/draft_PAPER'
path = '../../SchemaBigFiles/_PaperOutputData'


# date = 20210930 # within subj

path = os.path.join(path,scoretype)
if not os.path.exists(path):
    print("...making directory: ", path)
    os.makedirs(path)    
else:
    print("...directory exists: ", path)

fname = '{date}_{roi}_{roi_id:04d}_{hem}_{scoretype}_{extra}_within_subj.h5'.format(date=date, roi=roi, roi_id=roi_id,
                                                            hem=hem, scoretype=scoretype,extra=extra)
fullpath = os.path.join(path, fname)

print('...Saving to ', fullpath)

data_labels = ['reinstatement_similarity_matrix',
              'story_effect',
              'schema_effect']

reinstatement_measures = [template_match, # nStories, nStories, 4, nSubj
                         story_effect, # (30,16,4,1001)
                         schema_effect] # (30,16,4,1001)

with h5py.File(fullpath, 'w') as hf:

    # create dict entry
    hf = hf.create_group(hem)
    
    # create sub-dict entries
    for label,measure in zip(data_labels,reinstatement_measures): 
        hf.create_dataset(label, data=measure)
        
print('...SAVING COMPLETE.')


print((time.time() - start_time)/60)



324
(324, 4) (324, 124)
VALID VERTS 1:  322
VALID VERTS 2:  322
...  [ True  True  True  True]
[1.54793834 1.16944732 1.7049941  1.6110709 ]
[[ 0.5706092   2.45629983  2.56408386 ...  1.36785183  0.40372297
  -0.21648872]
 [ 0.32519432 -0.74569297 -1.09441554 ... -0.64055315 -0.41633359
   0.28976388]
 [ 1.32579084  0.22538354 -0.33344587 ...  0.14332422  0.15192193
   0.50707946]
 ...
 [-0.35659097 -0.43216839  0.46468433 ...  0.32005629  1.24149541
   0.91608706]
 [-1.44970132 -1.13901182 -0.6532127  ... -1.32873059 -1.40893389
  -1.89291633]
 [ 1.04803588 -0.47106017  0.3049802  ...  0.51619245  0.78303619
   0.72461746]]
0 0 0
TEMPLATE match:  False
VALID VERTS 2:  322
...  [ True  True  True  True]
[1.54793834 1.16944732 1.7049941  1.6110709 ]
[[ 0.245278    2.22712701  4.10460871 ...  0.52915581 -0.30935405
  -0.85362253]
 [-0.92409056  0.98358049 -0.52714256 ... -0.9616527  -0.23462812
  -0.0660225 ]
 [ 0.03997275  1.29676426  1.27312901 ...  2.7211399   1.75643268
   1.12352546

0 0 0
TEMPLATE match:  False
VALID VERTS 2:  322
...  [ True  True  True  True]
[1.65343335 1.91292319 1.65247818 1.7271408 ]
[[ 0.37922088 -0.45206772  1.81563485 ...  0.55003926  0.11034568
  -0.27918583]
 [ 0.56174892  0.22516314  0.16174481 ...  0.01558883 -0.33610718
  -0.16109573]
 [ 1.31803533  0.74003544  0.65922248 ...  0.20752019 -0.58304527
  -1.07010504]
 ...
 [-1.13754729  0.84268007 -0.36810298 ...  0.91842828  0.8489029
   0.95036418]
 [-2.30898508 -0.8777974  -1.52935447 ... -0.7875206  -1.17006505
  -0.34800327]
 [ 0.05152178  0.09060711  0.49238791 ... -0.07964527  0.35943572
   0.21868948]]
0 0 0
TEMPLATE match:  False
VALID VERTS 2:  322
...  [ True  True  True  True]
[1.65343335 1.91292319 1.65247818 1.7271408 ]
[[-0.37298399 -1.60920613  1.0685634  ...  0.83112558  0.53013459
  -0.52211172]
 [-1.0208787  -1.02214319  0.48021452 ...  1.64217363  2.10400508
   1.56275431]
 [-2.73475211  1.59475073 -0.24227319 ...  2.80599177  3.36763704
   2.76968156]
 ...
 [ 0.3157

[[ 0.53219591  0.9580411   1.55302123 ... -0.08114941 -0.40727329
  -0.59896735]
 [-0.53973607 -0.01761173 -0.66239937 ...  0.96738256  0.72424525
   0.65510856]
 [ 0.11025621 -0.00350477 -0.47376236 ... -0.69965711 -0.71829046
  -0.32229628]
 ...
 [-0.61797082  2.25147422  0.31327299 ... -0.23033611 -0.32506589
  -0.98002957]
 [-0.01698359 -0.68647467 -0.03746258 ...  0.21830984 -0.06212901
   0.03001242]
 [ 1.80097915  2.00227428  3.46716139 ...  0.40284593 -1.04394088
  -0.45549903]]
0 0 0
TEMPLATE match:  False
VALID VERTS 2:  322
...  [ True  True  True  True]
[1.79921403 1.43199844 1.85476964 1.80557032]
[[ 0.32613787  1.80759575  1.9064594  ...  0.65192346  0.03441535
   0.01261553]
 [-0.49933986  0.651722   -0.74850961 ...  1.57747931  0.92983543
   0.55544613]
 [-0.79728914 -1.29473188 -0.34956714 ... -1.04248529 -0.0721323
  -0.27677795]
 ...
 [ 0.88273809 -0.42891446 -0.25249322 ... -1.3962735  -0.59747487
  -0.31125205]
 [-1.24031464 -0.95873088 -0.05500639 ... -0.38954326 

0 0 0
TEMPLATE match:  False
VALID VERTS 2:  322
...  [ True  True  True  True]
[1.76456473 1.62938415 1.65552272 1.3202296 ]
[[ 1.42554691  1.80939892  3.35796177 ...  0.92222832  0.73283123
   0.25480675]
 [-0.97080862  0.75683337 -0.26324794 ...  0.25412174 -0.16442119
  -0.71403194]
 [-0.30934762 -0.43145351  0.33473803 ... -0.66462781 -1.45152267
  -1.79651922]
 ...
 [-0.55118404 -0.1813327  -0.18686742 ...  1.23342209  1.09222542
   1.39174522]
 [-0.22559902 -1.28980388 -1.19797222 ... -1.07774411  0.10339027
   0.70188526]
 [-0.95870259  0.83251511  0.57680672 ...  0.09022742  0.6056582
   0.82325092]]
0 0 0
TEMPLATE match:  False
(324, 4) (324, 118)
VALID VERTS 1:  320
VALID VERTS 2:  320
...  [ True  True  True  True]
[1.8453253  1.83809197 1.66706921 1.84667149]
[[ 0.5706092   2.45629983  2.56408386 ...  1.95090617  1.36785183
   0.40372297]
 [ 0.32519432 -0.74569297 -1.09441554 ... -1.13766638 -0.64055315
  -0.41633359]
 [ 1.32579084  0.22538354 -0.33344587 ...  0.26459149  

(324, 4) (324, 127)
VALID VERTS 1:  322
VALID VERTS 2:  322
...  [ True  True  True  True]
[1.67597974 1.74791916 1.69877767 1.70517854]
[[ 0.5706092   2.45629983  2.56408386 ...  1.36785183  0.40372297
  -0.21648872]
 [ 0.32519432 -0.74569297 -1.09441554 ... -0.64055315 -0.41633359
   0.28976388]
 [ 1.32579084  0.22538354 -0.33344587 ...  0.14332422  0.15192193
   0.50707946]
 ...
 [-0.35659097 -0.43216839  0.46468433 ...  0.32005629  1.24149541
   0.91608706]
 [-1.44970132 -1.13901182 -0.6532127  ... -1.32873059 -1.40893389
  -1.89291633]
 [ 1.04803588 -0.47106017  0.3049802  ...  0.51619245  0.78303619
   0.72461746]]
0 0 0
TEMPLATE match:  False
VALID VERTS 2:  322
...  [ True  True  True  True]
[1.67597974 1.74791916 1.69877767 1.70517854]
[[ 0.245278    2.22712701  4.10460871 ...  0.52915581 -0.30935405
  -0.85362253]
 [-0.92409056  0.98358049 -0.52714256 ... -0.9616527  -0.23462812
  -0.0660225 ]
 [ 0.03997275  1.29676426  1.27312901 ...  2.7211399   1.75643268
   1.12352546]
 .

...

[[ 0.18088189 -0.34739074 -1.06052851 ...  0.48914696  0.33912998
   0.55064299]
 [-0.90321886  1.0468283  -0.33825319 ... -0.11857529 -0.33364837
  -0.19608239]
 [-0.87718784  1.617344    0.79156834 ... -0.41899661 -0.33918986
  -0.29812695]
 ...
 [ 1.25717616 -1.06182599 -0.14841573 ...  0.630525    0.53017464
   0.32248084]
 [ 1.30179139 -1.63675659 -1.63375348 ... -0.54793908 -0.7404352
  -0.44818704]
 [ 0.33506385  0.25348587 -1.31252469 ... -0.28299949  0.00500746
   0.01986259]]
0 0 0
TEMPLATE match:  False
VALID VERTS 2:  324
...  [ True  True  True  True]
[1.39323534 1.48834185 1.24289289 1.56016756]
[[ 0.5452355   0.37991684  1.83290553 ... -0.2386021  -0.52897848
  -0.03890737]
 [ 2.1455488  -0.32850325 -1.47764573 ...  1.85053947  1.74285362
   2.20936009]
 [ 0.45571826  0.44680549  0.12502412 ... -2.1204608  -1.69494174
  -2.54503661]
 ...
 [ 0.4999883  -0.15258291  0.47152974 ...  0.38571773  0.47799208
   0.508694  ]
 [ 0.70108326 -2.28381556 -0.97992014 ... -1.73670633 

0 0 0
TEMPLATE match:  False
VALID VERTS 2:  324
...  [ True  True  True  True]
[1.33953155 1.3574237  1.10764884 1.77432614]
[[ 0.572288   -0.31939324 -0.31507632 ... -0.70794421 -0.34440231
  -0.60204148]
 [-1.38153822  0.2527828   1.37476251 ...  1.1930275   1.20105738
   0.77552367]
 [-0.77035771  0.48288325 -0.79316921 ...  0.06807244 -0.15123403
  -0.28305925]
 ...
 [-0.27710389 -0.74924122  0.65248984 ... -0.9277619  -1.00656112
  -1.09215587]
 [ 0.39850044 -0.25331975  0.60127049 ... -0.57721184 -0.74696958
  -0.67360957]
 [-0.33736155  0.6603802  -0.59425817 ...  0.24194581 -0.04327886
   0.44443316]]
0 0 0
TEMPLATE match:  False
VALID VERTS 2:  324
...  [ True  True  True  True]
[1.33953155 1.3574237  1.10764884 1.77432614]
[[-0.05048153  1.20030557 -0.16264943 ... -0.97841666 -1.1427008
  -0.89556169]
 [ 1.45789477 -1.32354613 -1.0612105  ...  1.6218373   1.87533512
   1.5455579 ]
 [-0.68703913  0.79128921  1.01155359 ...  2.49331691  2.69704167
   2.77922019]
 ...
 [-0.8970

0 0 0
TEMPLATE match:  False
VALID VERTS 2:  324
...  [ True  True  True  True]
[1.29874213 0.94178992 1.70666851 1.59982892]
[[ 0.572288   -0.31939324 -0.31507632 ... -0.70794421 -0.34440231
  -0.60204148]
 [-1.38153822  0.2527828   1.37476251 ...  1.1930275   1.20105738
   0.77552367]
 [-0.77035771  0.48288325 -0.79316921 ...  0.06807244 -0.15123403
  -0.28305925]
 ...
 [-0.27710389 -0.74924122  0.65248984 ... -0.9277619  -1.00656112
  -1.09215587]
 [ 0.39850044 -0.25331975  0.60127049 ... -0.57721184 -0.74696958
  -0.67360957]
 [-0.33736155  0.6603802  -0.59425817 ...  0.24194581 -0.04327886
   0.44443316]]
0 0 0
TEMPLATE match:  False
VALID VERTS 2:  324
...  [ True  True  True  True]
[1.29874213 0.94178992 1.70666851 1.59982892]
[[-0.05048153  1.20030557 -0.16264943 ... -0.97841666 -1.1427008
  -0.89556169]
 [ 1.45789477 -1.32354613 -1.0612105  ...  1.6218373   1.87533512
   1.5455579 ]
 [-0.68703913  0.79128921  1.01155359 ...  2.49331691  2.69704167
   2.77922019]
 ...
 [-0.8970

(324, 4) (324, 116)
VALID VERTS 1:  324
VALID VERTS 2:  324
...  [ True  True  True  True]
[0.75189228 1.46323554 1.21231063 1.93429164]
[[ 0.85030697  0.10541308  0.18975336 ...  1.00363828  1.28314719
   0.75553487]
 [-1.7294527  -0.25655492 -0.28084655 ...  0.18988373 -0.24065552
   0.03960013]
 [-0.62274176 -0.63649143 -0.17310423 ... -0.63878964 -0.90136988
  -0.50372036]
 ...
 [-0.0671687   1.31381223  1.85406482 ...  1.14666071  1.6714281
   0.71311501]
 [-0.04697869  0.17840775 -0.08892482 ...  1.06774875  0.85653092
   1.32600386]
 [-1.09483587  0.53024302 -0.73329107 ... -1.11111278 -1.5313879
  -0.99520187]]
0 0 0
TEMPLATE match:  False
VALID VERTS 2:  324
...  [ True  True  True  True]
[0.75189228 1.46323554 1.21231063 1.93429164]
[[ 1.27098281 -0.14078165 -1.87110908 ...  0.64486869  0.78860135
   0.79796403]
 [-1.47676498  0.40056135 -0.11302297 ...  1.67366898  1.64341295
   1.68812685]
 [ 2.59890479 -1.12221844  0.21333076 ...  0.37862256  0.56431049
   0.43797365]
 ...

...directory exists:  ../../SchemaBigFiles/_PaperOutputData/sl_recall_score
...Saving to  ../../SchemaBigFiles/_PaperOutputData/sl_recall_score/20211014_SL_0022_R_sl_recall_score_within_modality_within_subj.h5
7.01254655122757


In [ ]:
ls -1t /jukebox/norman/rmasis/clones/SchemaBigFiles/draft_PAPER/LOGS -n 5

In [9]:
cat /jukebox/norman/rmasis/clones/SchemaBigFiles/draft_PAPER/LOGS/slurm_-24526524.log

DATE LABEL 20211014
HEM R
ROI SL
ROI_ID 1478
SCORETYPE sl_percept_score
EXTRA within_modality
...directory exists:  ../../SchemaBigFiles/_PaperOutputData/sl_percept_score
...Saving to  ../../SchemaBigFiles/_PaperOutputData/sl_percept_score/20211014_SL_1478_R_sl_percept_score_within_modality_within_subj.h5
...SAVING COMPLETE.


# WITHIN SUBJ PERCEPT SCORES (figure out issue with subj 19)

In [40]:

import sys
# sys.path.append('../')
# #import time

import numpy as np
import deepdish as dd
import os
from scipy.stats import zscore

import nibabel as nib #use to load mmp atlas
# from itertools import compress #dont think i use this. probably not necessary
import h5py

from _deconvolve import *

from _functions import * #import the story schema effect scoring function



################
################ INPUTS
################

# date = sys.argv[1] # 'date label to use'
# hem = str(sys.argv[2]) # 'L' or 'R'
# roi = sys.argv[3] # 'STS', 'SL', 'atlas'
# roi_id = int(sys.argv[4]) # "9999" or int
# scoretype = sys.argv[5] # "sl_percept_scores" or any directory name that makes sense
# extra = sys.argv[6] #within_modality


date = 20211014 #sys.argv[1] # 'date label to use'
hem = 'L' #str(sys.argv[2]) # 'L' or 'R'
roi = 'Ang' #sys.argv[3] # 'STS', 'SL', 'atlas'
roi_id = 9999 #int(sys.argv[4]) # "9999" or int
scoretype = 'roi_percept_score' #sys.argv[5] # "sl_percept_scores" or any directory name that makes sense
extra = 'within_modality' #sys.argv[6] #within_modality



################
################ CONSTANTS
################

nSubj = 31 # perception has 31 subj
TR = 1.5
nStories = len(stories)
nEvents = 4
nPerm = 1
nv = 40962

################
################ RUN ANALYSIS
################

### load perception templates
percept_dirname = '{}_percept_score'.format(scoretype.split('_')[0].lower())
# path = '../SchemaBigFiles/draft_PAPER/{}'.format(percept_dirname)
path = '../../SchemaBigFiles/_PaperOutputData/{}'.format(percept_dirname)

fname = '{date}_{roi}_{roi_id:04d}_{hem}_{percept_dirname}_{extra}.h5'.format(date=date, roi=roi, roi_id=roi_id,
                                                            hem=hem, percept_dirname=percept_dirname,extra=extra)
fullpath = os.path.join(path, fname)
# story_templates = dd.io.load(fullpath, '/' + hem + '/' + 'group_event_templates')
story_templates = dd.io.load(fullpath, '/' + hem + '/' + 'subj_event_templates') #for individual subject analysis, i think.



### RUN SIMILARITY MATRIX (within subj for schema score)
within_subj_smat = np.zeros((nStories,nStories,nEvents,nSubj))
for s in range(nSubj):
    story_ev_patterns = story_templates[s,:,:,:] 
    
    for ev in range(nEvents):
        valid_verts = np.all(~np.isnan(story_templates[s,:,:,:]),0)[:,ev] #nov 22, 2021
        within_subj_smat[:,:,ev,s] = np.corrcoef(story_ev_patterns[:,valid_verts,ev], story_ev_patterns[:,valid_verts,ev])[:16,16:]
        
        
### RUN STORY AND SCHEMA SCORING (although STORY score pointless here)
nEvents= 4
story_effect = np.zeros((nSubj,nStories,nEvents,nPerm+1)) 
schema_effect = np.zeros((nSubj,nStories,nEvents,nPerm+1)) 

for ev in range(nEvents):
    story_effect[:,:,ev,:], schema_effect[:,:,ev,:] = GetStorySchemaEffect(within_subj_smat[:,:,ev,:],nPerm=nPerm)
    
################
################ FILE SAVING 
################

# path = '/jukebox/norman/rmasis/clones/SchemaBigFiles/draft_PAPER'
path = '../../SchemaBigFiles/_PaperOutputData'


# if roi in ['mPFC', 'PMC', 'Aud', 'MTN', 'PM', 'MP','AT','STS','SFG']:
#     savedir = 'roi_{}'.format(scoretype)
# elif roi == 'atlas':
#     savedir = 'roi_{}'.format(scoretype)
# elif roi.lower() == 'sl':
#     savedir = 'sl_{}'.format(scoretype)

path = os.path.join(path,scoretype)
if not os.path.exists(path):
    print("...making directory: ", path)
    os.makedirs(path)    
else:
    print("...directory exists: ", path)
    
    
data_labels = [
               'loo_event_similarity_matrix', 
               'story_effect',
               'schema_effect']

perception_measures = [
                       
                       within_subj_smat,  # (16,16,4,31) #N-1 spatial ISC 
                       story_effect, 
                       schema_effect]

# date = 20210930 #for within subj

fname = '{date}_{roi}_{roi_id:04d}_{hem}_{scoretype}_{extra}_within_subj.h5'.format(date=date, roi=roi, roi_id=roi_id,
                                                            hem=hem, scoretype=scoretype,extra=extra)
fullpath = os.path.join(path, fname)
print('...Saving to ', fullpath)

# with h5py.File(fullpath, 'w') as hf:

#     # create dict entry
#     hf = hf.create_group(hem)
    
#     # create sub-dict entries
#     for label,measure in zip(data_labels,perception_measures): 
#         hf.create_dataset(label, data=measure)
        
# print('...SAVING COMPLETE.')

            

()
()
()
()
()
()
()
()
()
()
()
()
()
()
()
()
()
()
()
()
()
()
()
()
()
()
()
()
()
()
()
...directory exists:  ../../SchemaBigFiles/_PaperOutputData/roi_percept_score
...Saving to  ../../SchemaBigFiles/_PaperOutputData/roi_percept_score/20211014_Ang_9999_L_roi_percept_score_within_modality_within_subj.h5


In [20]:
np.isnan(story_templates[has_R][19,2,:,0]).sum()#.shape#.shape

31

In [35]:
np.all(~np.isnan(story_templates[s,:]),0)[:,0].sum()

1120

In [39]:
np.all(~np.isnan(story_ev_patterns[:]),0)[:,ev].shape

(1120,)

In [23]:
story_templates.shape

(31, 16, 1120, 4)

In [21]:
1120 -31

1089

In [43]:
np.where(np.isnan(story_templates[has_R][19,:,:]))

(array([ 2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,
         2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,
         2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,
         2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,
         2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,
         2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,
         2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,
         2,  2,  2,  2,  2,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,
         6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,
         6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,
         6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,
         6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,
         6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,  6,
         6, 

In [41]:
np.nanmean(story_effect[has_R][:,:,:,0],2)

array([[0.93401674, 0.94966734, 0.97688747, 0.9317558 , 1.02016086,
        0.93019691, 1.05655802, 1.01691203, 0.92394106, 0.94839582,
        0.9146246 , 0.98235797, 0.86378223, 1.08987082, 0.89597341,
        0.89489943],
       [0.84205598, 0.89671303, 0.91521251, 1.0141077 , 1.00599842,
        0.98329257, 0.95118008, 0.99881274, 0.80413705, 0.75893189,
        1.06392843, 0.84675655, 1.03497623, 1.14434965, 0.8503762 ,
        0.93813554],
       [0.68356334, 0.86461871, 0.71766571, 0.6499096 , 1.11117759,
        0.94905777, 1.07698351, 0.94867039, 1.05477365, 1.06436494,
        1.15767058, 0.92570199, 0.99030515, 0.75247495, 0.73041161,
        0.74006523],
       [0.87170519, 0.85487786, 0.77292662, 0.86983972, 0.69903417,
        0.82972537, 0.75316803, 0.93428859, 0.79724076, 0.94277234,
        0.84947444, 0.78689007, 0.81868301, 0.8191795 , 0.85562579,
        0.9552682 ],
       [1.06274022, 0.84923654, 1.04621794, 0.86474149, 0.93702382,
        1.01602044, 1.04232741, 

In [33]:
np.where(np.isnan(story_effect))

(array([20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20,
        20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20,
        20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20]),
 array([ 1,  1,  1,  2,  2,  2,  2,  2,  2,  2,  2,  4,  4,  5,  6,  6,  6,
         6,  6,  6,  6,  6,  8, 10, 10, 10, 10, 10, 10, 10, 10, 11, 11, 12,
        13, 14, 14, 14, 14, 14, 14, 14, 14, 15, 15]),
 array([0, 1, 3, 0, 0, 1, 1, 2, 2, 3, 3, 0, 2, 1, 0, 0, 1, 1, 2, 2, 3, 3,
        3, 0, 0, 1, 1, 2, 2, 3, 3, 1, 2, 0, 3, 0, 0, 1, 1, 2, 2, 3, 3, 1,
        2]),
 array([1, 1, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 1, 1, 0, 1, 0, 1, 0, 1, 0, 1,
        1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 1, 1, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1,
        1]))

# PREDICTIONS



In [23]:

from _functions import * #includes constants and score function
import sys
import deepdish as dd
import numpy as np
import os
import h5py
from scipy.stats import pearsonr

################
################ INPUTS
################


date = 20211014 #sys.argv[1] # 'date label to use'
hem = 'L' #str(sys.argv[2]) # 'L' or 'R'
roi = 'Ang' #sys.argv[3] # 'STS', 'SL', 'atlas'
roi_id = 9999 #int(sys.argv[4]) # "9999" or int
scoretype = 'roi_percept_score' #sys.argv[5] # "sl_percept_scores" or any directory name that makes sense
extra = 'within_modality_within_subj' #sys.argv[6] #within_modality



# date = sys.argv[1] # 'date label to use'
# hem = str(sys.argv[2]) # 'L' or 'R'
# roi = sys.argv[3] # 'STS', 'SL', 'atlas'
# roi_id = int(sys.argv[4]) # "9999" or int
# scoretype = sys.argv[5] # "sl_percept_scores" or any directory name that makes sense
# try:
#     extra = sys.argv[6] #'_WithinSubj'/across modality
# except:
#     extra = ''

# datapath = '/jukebox/norman/rmasis/clones/SchemaBigFiles/draft_PAPER/roi_percept_score'
# savepath = '/jukebox/norman/rmasis/clones/SchemaBigFiles/draft_PAPER/roi_predictions'
# fname = 


################
################ CONSTANTS 
################

nSubj = 30

### import rubric scores
rubric_scores = openObject('normalizedRubricScores_byStory.pkl')

################
################ FUNCTIONS
################

def GetStorySchemaScore(date,roi,roi_id,hem,scoretype,event='all'):


#     path = '../SchemaBigFiles/draft_PAPER/{}'.format(scoretype)
    
    path = '../../SchemaBigFiles/_PaperOutputData/{}'.format(scoretype)


    subj_selection = has_R if 'percept' in scoretype.split('_') else np.full(30,fill_value=True) #recalls only have 30 subj

    fname = '{date}_{roi}_{roi_id:04d}_{hem}_{scoretype}_{extra}.h5'.format(date=date, roi=roi, roi_id=roi_id,
                                                                hem=hem, scoretype=scoretype,extra=extra)

    score = {}
    for eff in ['story_effect','schema_effect']:
        score[eff] = dd.io.load(os.path.join(path,fname), '/' + hem + '/'+ eff )[subj_selection,:]
        
        if event=='all':
            score[eff] = np.nanmean(score[eff][:,:,:,0],axis=2) #average out the event dimension, select raw data (not permtuation)
        else:
            score[eff] = score[eff][:,:,event,0]
        
    return score

################
################ RUN ANALYSIS
################

### our 'X' in the regression
input_scores = GetStorySchemaScore(date,roi,roi_id,hem,scoretype,event='all')

# # # ## import the outcome variable of choice, the 'Y' in our regression
fname = 'normalizedRubricScores_byStory.pkl'
modeltype = 'predict_rubric' #for file saving purposes
outcome_scores = openObject(fname) 

# import the outcome variable of choice, the 'Y' in our regression
# fname = 'raw_wv_schema.pkl'
# modeltype = 'predict_raw_wv_schema' #for file saving purposes
# outcome_scores = openObject(fname) 

# # import the outcome variable of choice, the 'Y' in our regression
# fname = 'raw_wv_story.pkl'
# modeltype = 'predict_raw_wv_story' #for file saving purposes
# outcome_scores = openObject(fname) 

# # # import the outcome variable of choice, the 'Y' in our regression
# fname = '0f_wv_schema.pkl'
# modeltype = 'predict_0f_wv_schema' #for file saving purposes
# outcome_scores = openObject(fname) 


# # import the outcome variable of choice, the 'Y' in our regression // # new schema effect 20200805
# fname = 'wv_euc_schema.pkl'
# modeltype = 'predict_wv_euc_schema' #for file saving purposes
# outcome_scores = openObject(fname) 

# # import the outcome variable of choice, the 'Y' in our regression // # new schema effect 20200805
# fname = 'wv_euc_story.pkl'
# modeltype = 'predict_wv_euc_story' #for file saving purposes
# outcome_scores = openObject(fname) 

# # import the outcome variable of choice, the 'Y' in our regression // # new schema effect 20200805
# fname = 'wv_gl_story.pkl'
# modeltype = 'predict_wv_gl_story' #for file saving purposes
# outcome_scores = openObject(fname) 

# # import the outcome variable of choice, the 'Y' in our regression // # new schema effect 20200805
# fname = 'wv_gl_schema.pkl'
# modeltype = 'predict_wv_gl_schema' #for file saving purposes
# outcome_scores = openObject(fname) 

# # import the outcome variable of choice, the 'Y' in our regression // # new schema effect 20200805
# fname = 'wv_bertsent_schema.pkl'
# modeltype = 'predict_wv_bertsent_schema' #for file saving purposes
# outcome_scores = openObject(fname) 

# # import the outcome variable of choice, the 'Y' in our regression // # new schema effect 20200805
# fname = 'wv_bertsent_story.pkl'
# modeltype = 'predict_wv_bertsent_story' #for file saving purposes
# outcome_scores = openObject(fname) 

# # import the outcome variable of choice, the 'Y' in our regression // # new schema effect 20200805
# fname = "wv_bertsent_corr_schemadescrdiff.pkl"
# modeltype = 'predict_wv_bertsent_corr_schemadescrdiff' #for file saving purposes
# outcome_scores = openObject(fname) 

# # import the outcome variable of choice, the 'Y' in our regression // # new schema effect 20200805
# fname = "wv_bertsent_euc_schemadescrdiff.pkl"
# modeltype = 'predict_wv_bertsent_euc_schemadescrdiff' #for file saving purposes
# outcome_scores = openObject(fname) 

# # import the outcome variable of choice, the 'Y' in our regression // # new schema effect 20200805
# fname = "wv_bertsent_rawcos_schema.pkl"
# modeltype = 'predict_wv_bertsent_rawcos_schema' #for file saving purposes
# outcome_scores = openObject(fname) 

# # import the outcome variable of choice, the 'Y' in our regression // # new schema effect 20200805
# fname = "wv_bertsent_rawcos_story.pkl"
# modeltype = 'predict_wv_bertsent_rawcos_story' #for file saving purposes
# outcome_scores = openObject(fname) 

# # import the outcome variable of choice, the 'Y' in our regression // # new schema effect 20200805
# fname = "wv_fasttext_centered_euc_schemadescrdiff.pkl"
# modeltype = 'predict_wv_fasttext_centered_euc_schemadescrdiff' #for file saving purposes
# outcome_scores = openObject(fname) 

# # import the outcome variable of choice, the 'Y' in our regression // # new schema effect 20200805
# fname = "wv_fasttext_notcentered_euc_schemadescrdiff.pkl"
# modeltype = 'predict_wv_fasttext_notcentered_euc_schemadescrdiff' #for file saving purposes
# outcome_scores = openObject(fname) 

# # import the outcome variable of choice, the 'Y' in our regression // # new schema effect 20200805
# fname = "wv_fasttext_centered_corr_schemadescrdiff.pkl"
# modeltype = 'predict_wv_fasttext_centered_corr_schemadescrdiff' #for file saving purposes <--- official currently
# outcome_scores = openObject(fname) 


# # import the outcome variable of choice, the 'Y' in our regression // # new schema effect 20200805
# fname = "loos_fasttext_loopca_schemadist.pkl"
# modeltype = 'predict_loos_fasttext_loopca_schemadist' #for file saving purposes
# outcome_scores = openObject(fname) 

### !!! last one used as of 20201018
# import the outcome variable of choice, the 'Y' in our regression // # new schema effect 20200805
# fname = "loos_fasttext_loopca_normrows_schemadist.pkl"
# modeltype = 'predict_loos_fasttext_loopca_normrows_schemadist' #for file saving purposes
# outcome_scores = openObject(fname) 

# # import the outcome variable of choice, the 'Y' in our regression // #20200812
# fname = 'wv_dist_schema.pkl'
# modeltype = 'predict_wv_dist_schema' #for file saving purposes
# outcome_scores = openObject(fname)

# import the outcome variable of choice, the 'Y' in our regression // #20200812
# fname = 'wv_fasttext_centered_cossim_schemadescrdiff.pkl'
# modeltype = 'predict_wv_fasttext_centered_cossim_schemadescrdiff' #for file saving purposes
# outcome_scores = openObject(fname)


### RUN PREDICTIONS

## regression arguments
fit_intercept = True ; remThresh = -1 ; alphaval = 0.00 #.5 #0.5 #1#5#0.1 #1 #5 #1.1 #.5 #1e-1 #1e-4 # 1e-9 

r2_scores = {}
coeffs = {}
for eff in ['story_effect','schema_effect']:
    r2_scores[eff] = np.zeros((nPerm+1))
    
    coeffs[eff] = np.zeros((nSubj,nPerm+1)) #store coefficients
    
    score_perm = input_scores[eff][:,:,np.newaxis].copy()

    for p in (range(nPerm+1)):
        
        print(p,end=' ') if p%100==0 else None
        
        if p == 0:
            ### MAKE predictions with raw data
            all_pred,all_true,all_baseline,test_r2s,regcoef,reginter = linear_reg(score_perm,
                                                                      outcome_scores,
                                                                      rubric_scores,
                                                                      fit_intercept=fit_intercept,
                                                                      remThresh = remThresh,
                                                                      alphain=alphaval,
                                                                        printr2=True)

            ### !!! kind of useless -- need to make sure that I check lowest common denominator for these
            x = all_pred[~np.isnan(all_pred)]
            y = all_true[~np.isnan(all_true)]
            base = all_baseline[~np.isnan(all_baseline)]

            r2 = get_r2(x,y,base)
            r2_scores[eff][p] = r2
            coeffs[eff][:,p] = regcoef # get back 30 coefficients for this regression for each 30 subj
            
#             coeffs[eff][p] = len(regcoef[regcoef>0])/ len(regcoef)
            
            print(regcoef)

        else:

            ### SHUFFLE STORIES
            score_perm = input_scores[eff][:,:,np.newaxis].copy()
            for s in range(nSubj):
                score_perm[s,:] = score_perm[s,np.random.permutation(nStories),:]


            ### MAKE PREDICTSONS with shuffled data
            all_pred,all_true,all_baseline,test_r2s,regcoef,reginter = linear_reg(score_perm,
                                                                      outcome_scores,
                                                                      rubric_scores,
                                                                      fit_intercept=fit_intercept,
                                                                      remThresh = remThresh,
                                                                      alphain=alphaval,
                                                                        printr2=True)
            x = all_pred[~np.isnan(all_pred)]
            y = all_true[~np.isnan(all_true)]
            base = all_baseline[~np.isnan(all_baseline)]

            r2 = get_r2(x,y,base)
            r2_scores[eff][p] = r2
            coeffs[eff][:,p] = regcoef 
#             coeffs[eff][p] = len(regcoef[regcoef>0])/ len(regcoef)
            print(regcoef)
            
            
#### correlate everything

corrs={}
for effect in ['story_effect','schema_effect']:
    x,y = nanxy(input_scores[effect].ravel(),outcome_scores.ravel()) #only look at valid values, some SLs might have nans for some subjects
    corrs[effect] = pearsonr(x,y)[0]
    
# corrs = {effect : pearsonr(input_scores[effect].ravel(), outcome_scores.ravel())[0] for effect in ['story_effect','schema_effect']}


################
################ SAVE DATA
################

# date = 20200712
# date = 20200715 #saving out correlations
# date = 20210315 #checking out cosine vs pearson
# date = 20200715 #using new mpfc clusters
# date = 20210909 #to get correct coefficient outputs for encoding vs retrieval <--- THIS IS NOW F'd up, doesnt contain coef of pure stuff, is now corresponding to 20210717 stuff
# date = 20210717 #corresponds to cr


# date= 20210929 #for original SLs with og data
# # date=20210930 #for within subject
# # date=20210931 #fro across modality
# date = 20210930 #within subj, but percept and recall scores are 2020626 with the "withinsubj" prefix

## USE THE DATE FROM THE INPUT FOR SAVING.

### make directory to save results if it doesnt already exist

path = '../../SchemaBigFiles/_PaperOutputData'

# if roi in ['mPFC', 'PMC', 'Aud', 'MTN', 'PM', 'MP','AT','STS','SFG']:
#     roitype = 'roi'
#     savedir = '{}_predictions'.format(scoretype)
# elif roi == 'atlas':
#     roitype = 'atlas'
#     savedir = '{}_predictions'.format(scoretype)
# elif roi.lower() == 'sl':
#     roitype='sl'
#     savedir = '{}_predictions'.format(scoretype)
    
path = os.path.join(path,'{}_predictions'.format(scoretype))
if not os.path.exists(path):
    print("...making directory: ", path)
    os.makedirs(path)    
else:
    print("...directory exists: ", path)
    
data_labels = ['story_effect','schema_effect']

fname = '{date}_{roi}_{roi_id:04d}_{hem}_{scoretype}_{modeltype}_{extra}.h5'.format(date=date, 
                                                                roi=roi, 
                                                                roi_id=roi_id,
                                                                hem=hem, 
                                                                scoretype=scoretype,
                                                                modeltype = modeltype,
                                                                extra = extra)
fullpath = os.path.join(path, fname)
print('...Saving to ', fullpath)

print("extra: ", extra)

with h5py.File(fullpath, 'w') as hf:

    # create dict entry
    hf = hf.create_group(hem)
    
    # create sub-dict entries
    for label in data_labels: 
        hf.create_dataset(label, data=r2_scores[label])
        
    ### save coeffs
    hf.create_dataset("story_coeff", data=coeffs['story_effect'])
    hf.create_dataset("schema_coeff", data=coeffs['schema_effect'])
    
    ##save corrs
    hf.create_dataset("story_corr", data=corrs['story_effect'])
    hf.create_dataset("schema_corr", data=corrs['schema_effect'])
        
print('...SAVING COMPLETE.')

0 

/jukebox/pkgs/PYGER/0.8/lib/python3.6/site-packages/ipykernel_launcher.py:70: RuntimeWarning: Mean of empty slice


ValueError: Input contains NaN, infinity or a value too large for dtype('float64').

In [22]:
input_scores['story_effect']

array([[0.93401674, 0.94966734, 0.97688747, 0.9317558 , 1.02016086,
        0.93019691, 1.05655802, 1.01691203, 0.92394106, 0.94839582,
        0.9146246 , 0.98235797, 0.86378223, 1.08987082, 0.89597341,
        0.89489943],
       [0.84205598, 0.89671303, 0.91521251, 1.0141077 , 1.00599842,
        0.98329257, 0.95118008, 0.99881274, 0.80413705, 0.75893189,
        1.06392843, 0.84675655, 1.03497623, 1.14434965, 0.8503762 ,
        0.93813554],
       [0.68356334, 0.86461871, 0.71766571, 0.6499096 , 1.11117759,
        0.94905777, 1.07698351, 0.94867039, 1.05477365, 1.06436494,
        1.15767058, 0.92570199, 0.99030515, 0.75247495, 0.73041161,
        0.74006523],
       [0.87170519, 0.85487786, 0.77292662, 0.86983972, 0.69903417,
        0.82972537, 0.75316803, 0.93428859, 0.79724076, 0.94277234,
        0.84947444, 0.78689007, 0.81868301, 0.8191795 , 0.85562579,
        0.9552682 ],
       [1.06274022, 0.84923654, 1.04621794, 0.86474149, 0.93702382,
        1.01602044, 1.04232741, 

In [25]:
input_scores['schema_effect'].shape

(30, 16)

In [26]:
np.where(np.isnan(input_scores['story_effect']))

(array([19, 19, 19, 19]), array([ 2,  6, 10, 14]))

In [47]:
input_scores['schema_effect'][19,10]

nan